# Setup 

In [1]:
!pip install transformers
!pip install datasets
!pip install huggingface_hub
!pip install seqeval 
!pip install evaluate --quiet
!pip install tf2crf

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 5.8 MB 4.7 MB/s 
     |████████████████████████████████| 7.6 MB 81.9 MB/s 
     |████████████████████████████████| 182 kB 90.1 MB/s 
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 451 kB 4.9 MB/s 
     |████████████████████████████████| 132 kB 87.4 MB/s 
     |████████████████████████████████| 212 kB 93.2 MB/s 
     |████████████████████████████████| 127 kB 84.8 MB/s 
  Attempting uninstall: urllib3
    Found existing installation: urllib3 1.24.3
    Uninstalling urllib3-1.24.3:
      Successfully uninstalled urllib3-1.24.3
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 4

In [2]:
from transformers import AutoTokenizer

from transformers import TFBertModel, TFAutoModelForTokenClassification, TFAutoModel
from datasets import load_dataset, load_metric

import numpy as np

import tensorflow as tf
import keras

from tensorflow.keras import Model, Input
from tensorflow.keras.layers import Embedding, Input, Dense, LSTM, Dropout, Bidirectional, Layer

from tf2crf import CRF
from tf2crf import ModelWithCRFLoss

from sklearn.metrics import f1_score, precision_score, recall_score, confusion_matrix
from tqdm.notebook import tqdm
from seqeval.metrics import classification_report

from tensorflow.keras.preprocessing.sequence import pad_sequences

np.random.seed(42)

# Functions

In [3]:
def get_padded_arr(inputs, max_length=180, pad_type='post', trunc_type='post'):
    """
    Returns a padded array from an input array, 
    padded to the max_length using pad_type and trunc_type.
    Uses pad_sequences() from tensorflow.keras.preprocessing.sequence.

    Parameters
    ----------
    inputs: nested list of ints
      input sequence of tokenized input_ids
    max_length: int
      maximum length to which to pad sequence
    pad_type: string
      padding type; ex: post, pre, etc.
    trunc_type: string
      truncation type; ex: post, pre, etc.

    Returns
    -------
    nested numpy array of ints
      numpy array of each numpy array of input_ids padded to max_length

    Example
    --------
    >>> get_padded_arr([[465, 1093, 669], [110, 549]], 5, 'post', 'post')
    array([[ 465, 1093,  669,    0,    0],
          [ 110,  549,    0,    0,    0]], dtype=int32)
    """

    padded_arr = pad_sequences(inputs, padding=pad_type, truncating=trunc_type, maxlen=max_length)
    input_arr = np.array([np.array(x) for x in padded_arr])

    return input_arr

In [4]:
def get_argmax_predictions(y_pred):
    """
    Returns an array of label predictions in the form of numpy arrays,
    from a vector of probability distributions output by softmax layer.

    Parameters
    ----------
    y_pred: nested list of floats
      vector of probability distributions created by softmax function

    Returns
    -------
    array of numpy array of ints
      array of predicted labels (numpy array) per example

    Example
    --------
    >>> get_argmax_predictions([[0.9, 0.05, 0.05], [0.04, 0.9, 0.06], 
                                [0.03, 0.07, 0.9], [0.9, 0.03, 0.07]])
    [0, 1, 2, 0]
    """

    predicted_labels = []
    for idx, input in enumerate(y_pred):
      input_preds = []
      for token in input:
        input_preds.append(np.argmax(token))
      predicted_labels.append(np.array(input_preds))

    return predicted_labels

In [5]:
def print_classification_report(test_labels, test_attention_mask, preds, label_names):
    """
    Prints the classification report with micro, macro, and weighted
    precision, recall, and f1_score for label classes found in the set.

    Parameters
    ----------
    test_labels: nested list of integers
      nested array of true labels sourced from dataset

    test_attention_mask: nested list of integers
      nested array of attention mask values created by tokenizer

    preds: nested list of integers
      nested array of predicted labels generated from model.predict()

    label_names: list of strings
      names of labels at their respective indices

    Returns
    -------
    Prints classification report, we use weighted average in our paper
    to represent the results, but we have micro and macro precision, recall,
    and f1 scores.
    """

    flatten_labels = []
    flatten_preds = []
    # Flatten true labels and predicted labels into one array each
    # to make comparison easily
    for i in tqdm(range(len(test_labels))):
      j = sum(test_attention_mask[i]).numpy() - 1
      flatten_labels.extend(test_labels[i][1:j])
      flatten_preds.extend(preds[i][1:j])
    flatten_labels = list(map(lambda x: label_names[x], flatten_labels))
    flatten_preds = list(map(lambda x: label_names[x], flatten_preds))

    # Generate precision, recall, and f1 scores
    # for overall labels.
    for s in classification_report([flatten_labels], [flatten_preds], digits=4).split('\n'):
      print(s)

# Load Datsets

In [6]:
## NCBI Dataset ## 
## Biomed Inform. 2014 February ; 47: 1–10. doi:10.1016/j.jbi.2013.12.006. 
## The NCBI Disease corpus consists of 793 PubMed abstracts, 
## which are separated into training (593), development (100) and test (100) subsets
## It includes 6,892 disease mentions, which are mapped to 790 unique disease concepts

ncbi_dataset = load_dataset("ncbi_disease")

Extracting data files #0:   0%|          | 0/1 [00:00<?, ?obj/s]

Extracting data files #1:   0%|          | 0/1 [00:00<?, ?obj/s]

Extracting data files #2:   0%|          | 0/1 [00:00<?, ?obj/s]

Generating train split:   0%|          | 0/5433 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/924 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/941 [00:00<?, ? examples/s]

Dataset ncbi_disease downloaded and prepared to /root/.cache/huggingface/datasets/ncbi_disease/ncbi_disease/1.0.0/92314c7992b0b8a5ea2ad101be33f365b684a2cc011e0ffa29c691e6d32b2d03. Subsequent calls will reuse this data.


  0%|          | 0/3 [00:00<?, ?it/s]

In [7]:
## GENE MENTION DATASET ##
## Genome Biology 2008, 9(Suppl 2):S2 

## BioCreative II Gene Mention Recognition (BC2GM) Dataset contains data 
## where participants are asked to identify a gene mention in a sentence 
## by giving its start and end characters. The training set consists of a 
## set of sentences, and for each sentence a set of gene mentions (GENE annotations).
## Includes  15,000 annotated training sentences.
## 

gm_dataset = load_dataset("bc2gm_corpus")

Extracting data files #0:   0%|          | 0/1 [00:00<?, ?obj/s]

Extracting data files #1:   0%|          | 0/1 [00:00<?, ?obj/s]

Extracting data files #2:   0%|          | 0/1 [00:00<?, ?obj/s]

Generating train split:   0%|          | 0/12501 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/2501 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/5001 [00:00<?, ? examples/s]

Dataset bc2gm_corpus downloaded and prepared to /root/.cache/huggingface/datasets/bc2gm_corpus/bc2gm_corpus/1.0.0/198658a8f6102c50f2230023a1fc49526139e3955e86bb62fafb48edfbbaca60. Subsequent calls will reuse this data.


  0%|          | 0/3 [00:00<?, ?it/s]

In [8]:
## CHEMICAL DISEASE RELATIONS DATASET ##
## Database, Volume 2016, 2016, baw068, https://doi.org/10.1093/database/baw068

## The BioCreative V CDR task corpus is manually annotated for chemicals,
## diseases and chemical-induced disease (CID) relations. 
## It consists of 1500 PubMed articles with 4409 annotated chemicals, 
## 5818 diseases and 3116 chemical-disease interactions.

cdr_dataset = load_dataset("ghadeermobasher/BC5CDR-Chemical-Disease")

Extracting data files #2:   0%|          | 0/1 [00:00<?, ?obj/s]

Extracting data files #1:   0%|          | 0/1 [00:00<?, ?obj/s]

Extracting data files #0:   0%|          | 0/1 [00:00<?, ?obj/s]

Generating train split: 0 examples [00:00, ? examples/s]

['Selegiline', '-', 'induced', 'postural', 'hypotension', 'in', 'Parkinson', "'", 's', 'disease', ':', 'a', 'longitudinal', 'study', 'on', 'the', 'effects', 'of', 'drug', 'withdrawal', '.']
['OBJECTIVES', ':', 'The', 'United', 'Kingdom', 'Parkinson', "'", 's', 'Disease', 'Research', 'Group', '(', 'UKPDRG', ')', 'trial', 'found', 'an', 'increased', 'mortality', 'in', 'patients', 'with', 'Parkinson', "'", 's', 'disease', '(', 'PD', ')', 'randomized', 'to', 'receive', '10', 'mg', 'selegiline', 'per', 'day', 'and', 'L', '-', 'dopa', 'compared', 'with', 'those', 'taking', 'L', '-', 'dopa', 'alone', '.']
['Recently', ',', 'we', 'found', 'that', 'therapy', 'with', 'selegiline', 'and', 'L', '-', 'dopa', 'was', 'associated', 'with', 'selective', 'systolic', 'orthostatic', 'hypotension', 'which', 'was', 'abolished', 'by', 'withdrawal', 'of', 'selegiline', '.']
['This', 'unwanted', 'effect', 'on', 'postural', 'blood', 'pressure', 'was', 'not', 'the', 'result', 'of', 'underlying', 'autonomic', 'fa

Generating validation split: 0 examples [00:00, ? examples/s]

['22', '-', 'oxacalcitriol', 'suppresses', 'secondary', 'hyperparathyroidism', 'without', 'inducing', 'low', 'bone', 'turnover', 'in', 'dogs', 'with', 'renal', 'failure', '.']
['BACKGROUND', ':', 'Calcitriol', 'therapy', 'suppresses', 'serum', 'levels', 'of', 'parathyroid', 'hormone', '(', 'PTH', ')', 'in', 'patients', 'with', 'renal', 'failure', 'but', 'has', 'several', 'drawbacks', ',', 'including', 'hypercalcemia', 'and', '/', 'or', 'marked', 'suppression', 'of', 'bone', 'turnover', ',', 'which', 'may', 'lead', 'to', 'adynamic', 'bone', 'disease', '.']
['A', 'new', 'vitamin', 'D', 'analogue', ',', '22', '-', 'oxacalcitriol', '(', 'OCT', ')', ',', 'has', 'been', 'shown', 'to', 'have', 'promising', 'characteristics', '.']
['This', 'study', 'was', 'undertaken', 'to', 'determine', 'the', 'effects', 'of', 'OCT', 'on', 'serum', 'PTH', 'levels', 'and', 'bone', 'turnover', 'in', 'states', 'of', 'normal', 'or', 'impaired', 'renal', 'function', '.']
['METHODS', ':', 'Sixty', 'dogs', 'were', '

Generating test split: 0 examples [00:00, ? examples/s]

['Torsade', 'de', 'pointes', 'ventricular', 'tachycardia', 'during', 'low', 'dose', 'intermittent', 'dobutamine', 'treatment', 'in', 'a', 'patient', 'with', 'dilated', 'cardiomyopathy', 'and', 'congestive', 'heart', 'failure', '.']
['The', 'authors', 'describe', 'the', 'case', 'of', 'a', '56', '-', 'year', '-', 'old', 'woman', 'with', 'chronic', ',', 'severe', 'heart', 'failure', 'secondary', 'to', 'dilated', 'cardiomyopathy', 'and', 'absence', 'of', 'significant', 'ventricular', 'arrhythmias', 'who', 'developed', 'QT', 'prolongation', 'and', 'torsade', 'de', 'pointes', 'ventricular', 'tachycardia', 'during', 'one', 'cycle', 'of', 'intermittent', 'low', 'dose', '(', '2', '.', '5', 'mcg', '/', 'kg', 'per', 'min', ')', 'dobutamine', '.']
['This', 'report', 'of', 'torsade', 'de', 'pointes', 'ventricular', 'tachycardia', 'during', 'intermittent', 'dobutamine', 'supports', 'the', 'hypothesis', 'that', 'unpredictable', 'fatal', 'arrhythmias', 'may', 'occur', 'even', 'with', 'low', 'doses', '

  0%|          | 0/3 [00:00<?, ?it/s]

In [9]:
print(ncbi_dataset['train'].shape)
print(ncbi_dataset['validation'].shape)
print(ncbi_dataset['test'].shape)

(5433, 3)
(924, 3)
(941, 3)


In [10]:
print(gm_dataset['train'].shape)
print(gm_dataset['validation'].shape)
print(gm_dataset['test'].shape)

(12501, 3)
(2501, 3)
(5001, 3)


In [11]:
print(cdr_dataset['train'].shape)
print(cdr_dataset['validation'].shape)
print(cdr_dataset['test'].shape)

(4561, 3)
(4582, 3)
(4798, 3)


# Model Definitions

In [228]:
# VANILLA BERT MODEL

def create_bert_model(num_labels, max_length=180, dropout=0.3) -> tf.keras.Model:
    """
    Creates a plain BERT model that takes in input_ids, attention_mask
    and will output a softmax probability distribution over a set of num_labels
    number of possible labels.

    Parameters
    ----------
    num_labels: integer
      the number of classes to compute the probabilities for
    max_length: int
      maximum length of inputs
    dropout: float
      dropout rate
    
    Returns
    -------
    a custom BERT model built on the pretrained bert-large-NER model
    for multi-class classification
    
    """
    bert_model = TFAutoModel.from_pretrained('dslim/bert-large-NER', num_labels=num_labels, ignore_mismatched_sizes=True)

    input_ids = Input(shape=(max_length,), dtype=tf.int64, name='input_ids')
    attention_mask = tf.keras.layers.Input(shape=(max_length,), dtype=tf.int64, name='attention_mask')

    bert_inputs = {'input_ids': input_ids,
                    'attention_mask': attention_mask}      

    bert_output = bert_model(bert_inputs)

    last_hidden_state = bert_output[0]

    embedding = tf.keras.layers.Dropout(dropout)(last_hidden_state)

    output = tf.keras.layers.Dense(num_labels, activation='softmax')(embedding)

    model = tf.keras.models.Model(inputs = [input_ids, attention_mask], outputs = output)
    model.compile(optimizer=tf.keras.optimizers.Adam(learning_rate=1e-5),
                        loss=tf.keras.losses.SparseCategoricalCrossentropy(), 
                        metrics=['accuracy'])

    return model

In [73]:
# VANILLA BIOBERT MODEL

def create_biobert_model(num_labels, max_length=180, dropout=0.3) -> tf.keras.Model:
    """
    Create a plain BioBERT model that takes in input_ids, attention_mask
    and will output a softmax probability distribution over a set of num_labels
    number of possible labels.

    Parameters
    ----------
    num_labels: integer
      the number of classes to compute the probabilities for
    max_length: int
      maximum length of inputs
    dropout: float
      dropout rate
    
    Returns
    -------
    a custom BioBERT model built on the pretrained biobert-base-cased-v1.1 model
    for multi-class classification
    
    """
    biobert_model = TFAutoModel.from_pretrained('dmis-lab/biobert-base-cased-v1.1', num_labels=num_labels, from_pt=True)

    input_ids = Input(shape=(max_length,), dtype=tf.int64, name='input_ids')
    attention_mask = tf.keras.layers.Input(shape=(max_length,), dtype=tf.int64, name='attention_mask')

    biobert_inputs = {'input_ids': input_ids,
                   'attention_mask': attention_mask}      

    biobert_output = biobert_model(biobert_inputs)

    last_hidden_state = biobert_output[0]

    embedding = tf.keras.layers.Dropout(dropout)(last_hidden_state)

    output = tf.keras.layers.Dense(num_labels, activation='softmax')(embedding)

    model = tf.keras.models.Model(inputs = [input_ids, attention_mask], outputs = output)
    model.compile(optimizer=tf.keras.optimizers.Adam(learning_rate= 5e-5),
                       loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True), 
                        metrics=['accuracy'])

    return model

In [ ]:
# BERT CRF MODEL

def create_bert_crf_model(num_labels, max_length=180) -> tf.keras.Model:
    """
    Create a layered BERT+CRF model that takes in input_ids, attention_mask
    and will output predicted labels for each example.

    Parameters
    ----------
    num_labels: integer
      the number of classes to compute the probabilities for
    max_length: int
      maximum length of inputs
    
    Returns
    -------
    a custom BERT+CRF layered model built on the pretrained 
    bert-large-NER model
    
    """
    bert_model = TFAutoModel.from_pretrained('dslim/bert-large-NER', num_labels=num_labels, ignore_mismatched_sizes=True)

    input_ids = Input(shape=(max_length,), dtype=tf.int64, name='input_ids')
    attention_mask = tf.keras.layers.Input(shape=(max_length,), dtype=tf.int64, name='attention_mask')

    bert_inputs = {'input_ids': input_ids,
                   'attention_mask': attention_mask}      

    bert_output = bert_model(bert_inputs)
    last_hidden_state = bert_output[0]
    crf_layer = CRF(num_labels)
    crf_out = crf_layer(last_hidden_state)
    base_model = keras.Model([input_ids, attention_mask], outputs=crf_out)

    # wrapping base model with ModelWithCRFLoss wrapper in order to use
    # CRF loss function from wrapper class
    model = ModelWithCRFLoss(base_model)
    model.compile(optimizer=tf.keras.optimizers.Adam(learning_rate= 1e-5), metrics=['accuracy'])

    return model

In [155]:
# BERT LSTM CRF MODEL

def create_bert_lstm_crf_model(num_labels, LSTM_units=64, max_length=180) -> tf.keras.Model:
    """
    Create a layered BERT+LSTM+CRF model that takes in input_ids, attention_mask
    and will output predicted labels for each example.

    Parameters
    ----------
    num_labels: integer
      the number of classes to compute the probabilities for
    LSTM_units: integer
      number of units representing the dimensionality of the output space
    max_length: int
      maximum length of inputs
    
    Returns
    -------
    a custom BERT+BiLSTM+CRF layered model built on the pretrained 
    bert-large-NER model
    
    """    
    bert_model = TFAutoModel.from_pretrained('dslim/bert-large-NER', num_labels=num_labels, ignore_mismatched_sizes=True)
    input_ids = Input(shape=(max_length,), dtype=tf.int64, name='input_ids')
    attention_mask = tf.keras.layers.Input(shape=(max_length,), dtype=tf.int64, name='attention_mask')

    bert_inputs = {'input_ids': input_ids,
                   'attention_mask': attention_mask}      

    bert_output = bert_model(bert_inputs)
    last_hidden_state = bert_output[0]

    lstm_layer = tf.keras.layers.LSTM(LSTM_units, return_sequences=True)(last_hidden_state)
    crf_layer = CRF(num_labels)
    crf_out = crf_layer(lstm_layer)
    base_model = keras.Model([input_ids, attention_mask], outputs=crf_out)
    model = ModelWithCRFLoss(base_model)
    model.compile(optimizer=tf.keras.optimizers.Adam(learning_rate= 1e-5), metrics=['accuracy'])

    return model

In [ ]:
# BERT BILSTM CRF MODEL

def create_bert_bilstm_crf_model(num_labels, LSTM_units=64, max_length=180) -> tf.keras.Model:
    """
    Create a layered BERT+BiLSTM+CRF model that takes in input_ids, attention_mask
    and will output predicted labels for each example.

    Parameters
    ----------
    num_labels: integer
      the number of classes to compute the probabilities for
    LSTM_units: integer
      number of units representing the dimensionality of the output space
    max_length: int
      maximum length of inputs
    
    Returns
    -------
    a custom BERT+BiLSTM+CRF layered model built on the pretrained 
    bert-large-NER model
    
    """    
    bert_model = TFAutoModel.from_pretrained('dslim/bert-large-NER', num_labels=num_labels, ignore_mismatched_sizes=True)
    input_ids = Input(shape=(max_length,), dtype=tf.int64, name='input_ids')
    attention_mask = tf.keras.layers.Input(shape=(max_length,), dtype=tf.int64, name='attention_mask')

    bert_inputs = {'input_ids': input_ids,
                   'attention_mask': attention_mask}      

    bert_output = bert_model(bert_inputs)
    last_hidden_state = bert_output[0]

    bilstm_layer = tf.keras.layers.Bidirectional(tf.keras.layers.LSTM(LSTM_units, return_sequences=True))(last_hidden_state)
    crf_layer = CRF(num_labels)
    crf_out = crf_layer(bilstm_layer)
    base_model = keras.Model([input_ids, attention_mask], outputs=crf_out)
    model = ModelWithCRFLoss(base_model)
    model.compile(optimizer=tf.keras.optimizers.Adam(learning_rate= 1e-5), metrics=['accuracy'])

    return model

In [104]:
# BIOBERT + CRF MODEL

def create_biobert_crf_model(num_labels, max_length=180) -> tf.keras.Model:
    """
    Create a layered BioBERT+CRF model that takes in input_ids, attention_mask
    and will output predicted labels for each example.

    Parameters
    ----------
    num_labels: integer
      the number of classes to compute the probabilities for
    max_length: int
      maximum length of inputs
    
    Returns
    -------
    a custom BioBERT+CRF layered model built on the pretrained 
    biobert-base-cased-v1.1 model
    
    """
    biobert_model = TFAutoModel.from_pretrained('dmis-lab/biobert-base-cased-v1.1', num_labels=num_labels, from_pt=True)

    input_ids = Input(shape=(max_length,), dtype=tf.int64, name='input_ids')
    attention_mask = tf.keras.layers.Input(shape=(max_length,), dtype=tf.int64, name='attention_mask')

    biobert_inputs = {'input_ids': input_ids,
                   'attention_mask': attention_mask}    
    biobert_output = biobert_model(biobert_inputs)

    last_hidden_state = biobert_output[0]

    crf_layer = CRF(num_labels)
    crf_out = crf_layer(last_hidden_state)
    base_model = keras.Model([input_ids, attention_mask], outputs=crf_out)
    model = ModelWithCRFLoss(base_model)
    model.compile(optimizer=tf.keras.optimizers.Adam(learning_rate= 5e-5), metrics=['accuracy'])

    return model

In [105]:
# BIOBERT + BiLSTM + CRF MODEL

def create_biobert_bilstm_crf_model(num_labels, LSTM_units=64, max_length=180):
    """
    Create a layered BioBERT+BiLSTM+CRF model that takes in input_ids, attention_mask
    and will output predicted labels for each example.

    Parameters
    ----------
    num_labels: integer
      the number of classes to compute the probabilities for
    LSTM_units: integer
      number of units representing the dimensionality of the output space
    max_length: int
      maximum length of inputs
    
    Returns
    -------
    a custom BioBERT+BiLSTM+CRF layered model built on the pretrained 
    biobert-base-cased-v1.1 model
    
    """   
    biobert_model = TFAutoModel.from_pretrained('dmis-lab/biobert-base-cased-v1.1', num_labels=num_labels, from_pt=True)

    input_ids = Input(shape=(max_length,), dtype=tf.int64, name='input_ids')
    attention_mask = tf.keras.layers.Input(shape=(max_length,), dtype=tf.int64, name='attention_mask')

    biobert_inputs = {'input_ids': input_ids,
                   'attention_mask': attention_mask}      

    biobert_output = biobert_model(biobert_inputs)
    last_hidden_state = biobert_output[0]

    bilstm_layer = tf.keras.layers.Bidirectional(tf.keras.layers.LSTM(LSTM_units, return_sequences=True))(last_hidden_state)
    crf_layer = CRF(num_labels)
    crf_out = crf_layer(bilstm_layer)
    base_model = keras.Model([input_ids, attention_mask], outputs=crf_out)
    model = ModelWithCRFLoss(base_model)
    model.compile(optimizer=tf.keras.optimizers.Adam(learning_rate= 5e-5), metrics=['accuracy'])

    return model

# Tokenization

In [74]:
# @title Create Unified Label Mapping Across Datasets
# rename "tags" to "ner_tags" for consistency
if 'tags' in cdr_dataset['train'].features.keys():
  cdr_dataset = cdr_dataset.rename_column("tags", "ner_tags")

# get labels from each dataset
ncbi_label_names = ncbi_dataset["train"].features["ner_tags"].feature.names
gm_label_names = gm_dataset["train"].features["ner_tags"].feature.names
cdr_label_names = ['O', 'B-Chemical', 'B-Disease', 'I-Disease', 'I-Chemical']

# create an unified label-to-index mapping across datasets
# keys: unique labels, values: indexes
label2index = {}
id = 0
for n in ncbi_label_names + gm_label_names + cdr_label_names:
  if n not in label2index:
    label2index[n] = id
    id += 1

label_names = list(label2index.keys())
label2index

from datasets import Features, Value, Sequence, ClassLabel
# define wanted output columns from the mapping process
# this ensures that the tokenized datasets have the same features for concatenation 
features = Features({
  'id': Value(dtype='string', id=None),
  'tokens': Sequence(feature=Value(dtype='string', id=None), length=-1, id=None),
  'ner_tags': Sequence(feature=ClassLabel(names=label_names, id=None), length=-1, id=None),
  'input_ids': Sequence(feature=Value(dtype='int32', id=None), length=-1, id=None),
  'token_type_ids': Sequence(feature=Value(dtype='int8', id=None), length=-1, id=None),
  'attention_mask': Sequence(feature=Value(dtype='int8', id=None), length=-1, id=None),
  'labels': Sequence(feature=Value(dtype='int64', id=None), length=-1, id=None)
})

bert_tokenizer = AutoTokenizer.from_pretrained("dslim/bert-base-NER")
# @title Map Labels To Tokenized Data (The Original Labels Were At Word-Level)
def bert_process(data, label_names):
  inputs = bert_tokenizer(data['tokens'], is_split_into_words=True, add_special_tokens=False)
  ner_tags = []
  for i, labels in enumerate(data['ner_tags']):
    word_ids = inputs.word_ids(i)
    label_ids = []
    for wid in word_ids:
      if wid is None: 
        label_ids.append(-100)
      else:
        label_ids.append(labels[wid])
    ner_tags.append(label_ids)
  inputs['labels'] = ner_tags
  return inputs

biobert_tokenizer = AutoTokenizer.from_pretrained("dmis-lab/biobert-base-cased-v1.1")
# @title Map Labels To Tokenized Data (The Original Labels Were At Word-Level)
def biobert_process(data, label_names):
  inputs = biobert_tokenizer(data['tokens'], is_split_into_words=True, add_special_tokens=False)
  ner_tags = []
  for i, labels in enumerate(data['ner_tags']):
    word_ids = inputs.word_ids(i)
    label_ids = []
    for wid in word_ids:
      if wid is None: 
        label_ids.append(-100)
      else:
        label_ids.append(labels[wid])
    ner_tags.append(label_ids)
  inputs['labels'] = ner_tags
  return inputs

Downloading:   0%|          | 0.00/313 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/213k [00:00<?, ?B/s]

In [75]:
#create BERT tokenized datasets
bert_tokenized_datasets = { 
    name: data.map(
      bert_process, 
      features=features,
      batched=True,
      fn_kwargs={
        'label_names': label_names,
        #'label2index': label2index,
      }
  ) for name, data, label_names in [
      ('ncbi', ncbi_dataset, ncbi_label_names),
      ('gm', gm_dataset, gm_label_names),
      ('cdr', cdr_dataset, cdr_label_names)
  ] 
}
#create bioBERT tokenized datasets
biobert_tokenized_datasets = { 
    name: data.map(
      biobert_process, 
      features=features,
      batched=True,
      fn_kwargs={
        'label_names': label_names,
        #'label2index': label2index,
      }
  ) for name, data, label_names in [
      ('ncbi', ncbi_dataset, ncbi_label_names),
      ('gm', gm_dataset, gm_label_names),
      ('cdr', cdr_dataset, cdr_label_names)
  ] 
}

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

  0%|          | 0/13 [00:00<?, ?ba/s]

  0%|          | 0/3 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/5 [00:00<?, ?ba/s]

  0%|          | 0/5 [00:00<?, ?ba/s]

  0%|          | 0/5 [00:00<?, ?ba/s]

# NCBI Dataset - Padding

In [76]:
# Create class label list
ncbi_label_list = ncbi_dataset["train"].features[f"ner_tags"].feature.names
ncbi_label_list

['O', 'B-Disease', 'I-Disease']

In [77]:
# examine the maximum length of any BERT tokenized inputs 
print(max([len(x) for x in bert_tokenized_datasets['ncbi']['train']['input_ids']]))
print(max([len(x) for x in bert_tokenized_datasets['ncbi']['validation']['input_ids']]))
print(max([len(x) for x in bert_tokenized_datasets['ncbi']['test']['input_ids']]))

176
120
155


In [78]:
# examine the maximum length of any BioBERT tokenized inputs
print(max([len(x) for x in biobert_tokenized_datasets['ncbi']['train']['input_ids']]))
print(max([len(x) for x in biobert_tokenized_datasets['ncbi']['validation']['input_ids']]))
print(max([len(x) for x in biobert_tokenized_datasets['ncbi']['test']['input_ids']]))

177
126
143


In [79]:
# declare NCBI specific global variables for model parameters
NCBI_MAX_LENGTH = 180
NCBI_NUM_LABELS = len(ncbi_label_list)

In [80]:
# create input and attention tensors using BERT tokenized datasets with max length
bert_ncbi_train_input_ids = tf.convert_to_tensor(get_padded_arr(bert_tokenized_datasets['ncbi']['train']['input_ids'], NCBI_MAX_LENGTH))
bert_ncbi_train_attention_mask = tf.convert_to_tensor(get_padded_arr(bert_tokenized_datasets['ncbi']['train']['attention_mask'], NCBI_MAX_LENGTH))

bert_ncbi_test_input_ids = tf.convert_to_tensor(get_padded_arr(bert_tokenized_datasets['ncbi']['test']['input_ids'], NCBI_MAX_LENGTH))
bert_ncbi_test_attention_mask = tf.convert_to_tensor(get_padded_arr(bert_tokenized_datasets['ncbi']['test']['attention_mask'], NCBI_MAX_LENGTH))

bert_ncbi_val_input_ids = tf.convert_to_tensor(get_padded_arr(bert_tokenized_datasets['ncbi']['validation']['input_ids'], NCBI_MAX_LENGTH))
bert_ncbi_val_attention_mask = tf.convert_to_tensor(get_padded_arr(bert_tokenized_datasets['ncbi']['validation']['attention_mask'], NCBI_MAX_LENGTH))

# create padded label arrays with max length
bert_ncbi_train_labels = get_padded_arr(bert_tokenized_datasets['ncbi']['train']['labels'], NCBI_MAX_LENGTH)
bert_ncbi_test_labels = get_padded_arr(bert_tokenized_datasets['ncbi']['test']['labels'], NCBI_MAX_LENGTH)
bert_ncbi_val_labels = get_padded_arr(bert_tokenized_datasets['ncbi']['validation']['labels'], NCBI_MAX_LENGTH)

In [81]:
# create input and attention tensors using BioBERT tokenized datasets with max length
biobert_ncbi_train_input_ids = tf.convert_to_tensor(get_padded_arr(biobert_tokenized_datasets['ncbi']['train']['input_ids'], NCBI_MAX_LENGTH))
biobert_ncbi_train_attention_mask = tf.convert_to_tensor(get_padded_arr(biobert_tokenized_datasets['ncbi']['train']['attention_mask'], NCBI_MAX_LENGTH))

biobert_ncbi_test_input_ids = tf.convert_to_tensor(get_padded_arr(biobert_tokenized_datasets['ncbi']['test']['input_ids'], NCBI_MAX_LENGTH))
biobert_ncbi_test_attention_mask = tf.convert_to_tensor(get_padded_arr(biobert_tokenized_datasets['ncbi']['test']['attention_mask'], NCBI_MAX_LENGTH))

biobert_ncbi_val_input_ids = tf.convert_to_tensor(get_padded_arr(biobert_tokenized_datasets['ncbi']['validation']['input_ids'], NCBI_MAX_LENGTH))
biobert_ncbi_val_attention_mask = tf.convert_to_tensor(get_padded_arr(biobert_tokenized_datasets['ncbi']['validation']['attention_mask'], NCBI_MAX_LENGTH))

# create padded label arrays with max length
biobert_ncbi_train_labels = get_padded_arr(biobert_tokenized_datasets['ncbi']['train']['labels'], NCBI_MAX_LENGTH)
biobert_ncbi_test_labels = get_padded_arr(biobert_tokenized_datasets['ncbi']['test']['labels'], NCBI_MAX_LENGTH)
biobert_ncbi_val_labels = get_padded_arr(biobert_tokenized_datasets['ncbi']['validation']['labels'], NCBI_MAX_LENGTH)

# Gene Mention Dataset - Padding

In [137]:
gm_label_list = gm_dataset["train"].features[f"ner_tags"].feature.names
gm_label_list

['O', 'B-GENE', 'I-GENE']

In [138]:
print(max([len(x) for x in bert_tokenized_datasets['gm']['train']['input_ids']]))
print(max([len(x) for x in bert_tokenized_datasets['gm']['validation']['input_ids']]))
print(max([len(x) for x in bert_tokenized_datasets['gm']['test']['input_ids']]))

277
295
287


In [139]:
print(max([len(x) for x in biobert_tokenized_datasets['gm']['train']['input_ids']]))
print(max([len(x) for x in biobert_tokenized_datasets['gm']['validation']['input_ids']]))
print(max([len(x) for x in biobert_tokenized_datasets['gm']['test']['input_ids']]))

276
291
280


In [140]:
GM_MAX_LENGTH = 295
GM_NUM_LABELS = len(gm_label_list)

In [141]:
bert_gm_train_input_ids = tf.convert_to_tensor(get_padded_arr(bert_tokenized_datasets['gm']['train']['input_ids'], GM_MAX_LENGTH))
bert_gm_train_attention_mask = tf.convert_to_tensor(get_padded_arr(bert_tokenized_datasets['gm']['train']['attention_mask'], GM_MAX_LENGTH))

bert_gm_test_input_ids = tf.convert_to_tensor(get_padded_arr(bert_tokenized_datasets['gm']['test']['input_ids'], GM_MAX_LENGTH))
bert_gm_test_attention_mask = tf.convert_to_tensor(get_padded_arr(bert_tokenized_datasets['gm']['test']['attention_mask'], GM_MAX_LENGTH))

bert_gm_val_input_ids = tf.convert_to_tensor(get_padded_arr(bert_tokenized_datasets['gm']['validation']['input_ids'], GM_MAX_LENGTH))
bert_gm_val_attention_mask = tf.convert_to_tensor(get_padded_arr(bert_tokenized_datasets['gm']['validation']['attention_mask'], GM_MAX_LENGTH))

bert_gm_train_labels = get_padded_arr(bert_tokenized_datasets['gm']['train']['labels'], GM_MAX_LENGTH)
bert_gm_test_labels = get_padded_arr(bert_tokenized_datasets['gm']['test']['labels'], GM_MAX_LENGTH)
bert_gm_val_labels = get_padded_arr(bert_tokenized_datasets['gm']['validation']['labels'], GM_MAX_LENGTH)

In [142]:
biobert_gm_train_input_ids = tf.convert_to_tensor(get_padded_arr(biobert_tokenized_datasets['gm']['train']['input_ids'], GM_MAX_LENGTH))
biobert_gm_train_attention_mask = tf.convert_to_tensor(get_padded_arr(biobert_tokenized_datasets['gm']['train']['attention_mask'], GM_MAX_LENGTH))

biobert_gm_test_input_ids = tf.convert_to_tensor(get_padded_arr(biobert_tokenized_datasets['gm']['test']['input_ids'], GM_MAX_LENGTH))
biobert_gm_test_attention_mask = tf.convert_to_tensor(get_padded_arr(biobert_tokenized_datasets['gm']['test']['attention_mask'], GM_MAX_LENGTH))

biobert_gm_val_input_ids = tf.convert_to_tensor(get_padded_arr(biobert_tokenized_datasets['gm']['validation']['input_ids'], GM_MAX_LENGTH))
biobert_gm_val_attention_mask = tf.convert_to_tensor(get_padded_arr(biobert_tokenized_datasets['gm']['validation']['attention_mask'], GM_MAX_LENGTH))

biobert_gm_train_labels = get_padded_arr(biobert_tokenized_datasets['gm']['train']['labels'], GM_MAX_LENGTH)
biobert_gm_test_labels = get_padded_arr(biobert_tokenized_datasets['gm']['test']['labels'], GM_MAX_LENGTH)
biobert_gm_val_labels = get_padded_arr(biobert_tokenized_datasets['gm']['validation']['labels'], GM_MAX_LENGTH)

# Chemical Disease Relation Dataset - Padding

In [170]:
cdr_label_list = cdr_dataset["train"].features[f"ner_tags"].feature.names
cdr_label_list

['O', 'B-Disease', 'I-Disease', 'B-Chemical', 'I-Chemical']

In [171]:
print(max([len(x) for x in bert_tokenized_datasets['cdr']['train']['input_ids']]))
print(max([len(x) for x in bert_tokenized_datasets['cdr']['validation']['input_ids']]))
print(max([len(x) for x in bert_tokenized_datasets['cdr']['test']['input_ids']]))

248
298
188


In [172]:
print(max([len(x) for x in biobert_tokenized_datasets['cdr']['train']['input_ids']]))
print(max([len(x) for x in biobert_tokenized_datasets['cdr']['validation']['input_ids']]))
print(max([len(x) for x in biobert_tokenized_datasets['cdr']['test']['input_ids']]))

249
298
185


In [173]:
CDR_MAX_LENGTH = 300
CDR_NUM_LABELS = len(cdr_label_list)

In [174]:
bert_cdr_train_input_ids = tf.convert_to_tensor(get_padded_arr(bert_tokenized_datasets['cdr']['train']['input_ids'], CDR_MAX_LENGTH))
bert_cdr_train_attention_mask = tf.convert_to_tensor(get_padded_arr(bert_tokenized_datasets['cdr']['train']['attention_mask'], CDR_MAX_LENGTH))

bert_cdr_test_input_ids = tf.convert_to_tensor(get_padded_arr(bert_tokenized_datasets['cdr']['test']['input_ids'], CDR_MAX_LENGTH))
bert_cdr_test_attention_mask = tf.convert_to_tensor(get_padded_arr(bert_tokenized_datasets['cdr']['test']['attention_mask'], CDR_MAX_LENGTH))

bert_cdr_val_input_ids = tf.convert_to_tensor(get_padded_arr(bert_tokenized_datasets['cdr']['validation']['input_ids'], CDR_MAX_LENGTH))
bert_cdr_val_attention_mask = tf.convert_to_tensor(get_padded_arr(bert_tokenized_datasets['cdr']['validation']['attention_mask'], CDR_MAX_LENGTH))

bert_cdr_train_labels = get_padded_arr(bert_tokenized_datasets['cdr']['train']['labels'], CDR_MAX_LENGTH)
bert_cdr_test_labels = get_padded_arr(bert_tokenized_datasets['cdr']['test']['labels'], CDR_MAX_LENGTH)
bert_cdr_val_labels = get_padded_arr(bert_tokenized_datasets['cdr']['validation']['labels'], CDR_MAX_LENGTH)

In [175]:
biobert_cdr_train_input_ids = tf.convert_to_tensor(get_padded_arr(biobert_tokenized_datasets['cdr']['train']['input_ids'], CDR_MAX_LENGTH))
biobert_cdr_train_attention_mask = tf.convert_to_tensor(get_padded_arr(biobert_tokenized_datasets['cdr']['train']['attention_mask'], CDR_MAX_LENGTH))

biobert_cdr_test_input_ids = tf.convert_to_tensor(get_padded_arr(biobert_tokenized_datasets['cdr']['test']['input_ids'], CDR_MAX_LENGTH))
biobert_cdr_test_attention_mask = tf.convert_to_tensor(get_padded_arr(biobert_tokenized_datasets['cdr']['test']['attention_mask'], CDR_MAX_LENGTH))

biobert_cdr_val_input_ids = tf.convert_to_tensor(get_padded_arr(biobert_tokenized_datasets['cdr']['validation']['input_ids'], CDR_MAX_LENGTH))
biobert_cdr_val_attention_mask = tf.convert_to_tensor(get_padded_arr(biobert_tokenized_datasets['cdr']['validation']['attention_mask'], CDR_MAX_LENGTH))

biobert_cdr_train_labels = get_padded_arr(biobert_tokenized_datasets['cdr']['train']['labels'], CDR_MAX_LENGTH)
biobert_cdr_test_labels = get_padded_arr(biobert_tokenized_datasets['cdr']['test']['labels'], CDR_MAX_LENGTH)
biobert_cdr_val_labels = get_padded_arr(biobert_tokenized_datasets['cdr']['validation']['labels'], CDR_MAX_LENGTH)




# BERT - NCBI

In [229]:
# create an instance of the BERT model with NCBI parameters
ncbi_bert_model = create_bert_model(NCBI_NUM_LABELS, NCBI_MAX_LENGTH)

Some layers from the model checkpoint at dslim/bert-large-NER were not used when initializing TFBertModel: ['classifier', 'dropout_73']
- This IS expected if you are initializing TFBertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFBertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
All the layers of TFBertModel were initialized from the model checkpoint at dslim/bert-large-NER.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFBertModel for predictions without further training.


In [230]:
# Train with sample train/validation dataset
history = ncbi_bert_model.fit([bert_ncbi_train_input_ids[:100], bert_ncbi_train_attention_mask[:100]], 
                                          bert_ncbi_train_labels[:100], batch_size=8, epochs=5, 
                                          validation_data=([bert_ncbi_val_input_ids[:100], bert_ncbi_val_attention_mask[:100]], bert_ncbi_val_labels[:100]))


Epoch 1/5


13/13 [==============================] - 44s 699ms/step - loss: 0.4397 - accuracy: 0.8646 - val_loss: 0.1622 - val_accuracy: 0.9777
Epoch 2/5
13/13 [==============================] - 3s 203ms/step - loss: 0.1784 - accuracy: 0.9658 - val_loss: 0.0732 - val_accuracy: 0.9774
Epoch 3/5
13/13 [==============================] - 3s 205ms/step - loss: 0.1020 - accuracy: 0.9649 - val_loss: 0.0579 - val_accuracy: 0.9824
Epoch 4/5
13/13 [==============================] - 3s 202ms/step - loss: 0.0965 - accuracy: 0.9665 - val_loss: 0.0458 - val_accuracy: 0.9853
Epoch 5/5
13/13 [==============================] - 3s 204ms/step - loss: 0.0599 - accuracy: 0.9809 - val_loss: 0.0420 - val_accuracy: 0.9869


In [231]:
ncbi_bert_model.summary()

Model: "model_32"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 attention_mask (InputLayer)    [(None, 180)]        0           []                               
                                                                                                  
 input_ids (InputLayer)         [(None, 180)]        0           []                               
                                                                                                  
 tf_bert_model_32 (TFBertModel)  TFBaseModelOutputWi  333579264  ['attention_mask[0][0]',         
                                thPoolingAndCrossAt               'input_ids[0][0]']              
                                tentions(last_hidde                                               
                                n_state=(None, 180,                                        

In [232]:
# Train with full train/validation dataset
history = ncbi_bert_model.fit([bert_ncbi_train_input_ids, bert_ncbi_train_attention_mask], 
                                          bert_ncbi_train_labels, batch_size=8, epochs=5, 
                                          validation_data=([bert_ncbi_val_input_ids, bert_ncbi_val_attention_mask], bert_ncbi_val_labels))


Epoch 1/5
680/680 [==============================] - 101s 149ms/step - loss: 0.0276 - accuracy: 0.9916 - val_loss: 0.0152 - val_accuracy: 0.9956
Epoch 2/5
680/680 [==============================] - 101s 148ms/step - loss: 0.0129 - accuracy: 0.9965 - val_loss: 0.0148 - val_accuracy: 0.9960
Epoch 3/5
680/680 [==============================] - 101s 148ms/step - loss: 0.0092 - accuracy: 0.9975 - val_loss: 0.0153 - val_accuracy: 0.9960
Epoch 4/5
680/680 [==============================] - 101s 149ms/step - loss: 0.0065 - accuracy: 0.9984 - val_loss: 0.0189 - val_accuracy: 0.9961
Epoch 5/5
680/680 [==============================] - 101s 148ms/step - loss: 0.0054 - accuracy: 0.9987 - val_loss: 0.0206 - val_accuracy: 0.9960


In [233]:
#loss, accuracy = ncbi_bert_model.evaluate([bert_ncbi_test_input_ids, bert_ncbi_test_attention_mask], bert_ncbi_test_labels, verbose=0)

# create predictions using test input_ids and attention_mask
bert_ncbi_predictions = ncbi_bert_model.predict([bert_ncbi_test_input_ids, bert_ncbi_test_attention_mask])

30/30 [==============================] - 10s 137ms/step


In [234]:
# for BERT, since model predictions is a softmax probability distribution
# over the number of classes, we need to use get_argmax_predictions
# to return predictions in a list of expected integer labels
bert_ncbi_preds_list = get_argmax_predictions(bert_ncbi_predictions)

In [235]:
# print the classification report
print_classification_report(bert_ncbi_test_labels, bert_ncbi_test_attention_mask, bert_ncbi_preds_list, ncbi_label_list)

  0%|          | 0/941 [00:00<?, ?it/s]

              precision    recall  f1-score   support

     Disease     0.8210    0.8779    0.8485      2220

   micro avg     0.8210    0.8779    0.8485      2220
   macro avg     0.8210    0.8779    0.8485      2220
weighted avg     0.8210    0.8779    0.8485      2220



# BioBERT - NCBI

In [110]:
ncbi_biobert_model = create_biobert_model(NCBI_NUM_LABELS, NCBI_MAX_LENGTH)

Some weights of the PyTorch model were not used when initializing the TF 2.0 model TFBertModel: ['cls.predictions.transform.dense.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.predictions.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing TFBertModel from a PyTorch model trained on another task or with another architecture (e.g. initializing a TFBertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFBertModel from a PyTorch model that you expect to be exactly identical (e.g. initializing a TFBertForSequenceClassification model from a BertForSequenceClassification model).
All the weights of TFBertModel were initialized from the PyTorch model.
If your task is similar to the task the model of the checkpoint

In [111]:
# Train with sample train/ validation dataset

history = ncbi_biobert_model.fit([biobert_ncbi_train_input_ids[:500], biobert_ncbi_train_attention_mask[:500]], 
                                          biobert_ncbi_train_labels[:500], batch_size=8, epochs=5, 
                                          validation_data=([biobert_ncbi_val_input_ids[:500], biobert_ncbi_val_attention_mask[:500]], biobert_ncbi_val_labels[:500]))


Epoch 1/5


63/63 [==============================] - 24s 138ms/step - loss: 0.1322 - accuracy: 0.9629 - val_loss: 0.0323 - val_accuracy: 0.9888
Epoch 2/5
63/63 [==============================] - 6s 90ms/step - loss: 0.0356 - accuracy: 0.9867 - val_loss: 0.0247 - val_accuracy: 0.9916
Epoch 3/5
63/63 [==============================] - 6s 89ms/step - loss: 0.0227 - accuracy: 0.9921 - val_loss: 0.0265 - val_accuracy: 0.9919
Epoch 4/5
63/63 [==============================] - 6s 89ms/step - loss: 0.0161 - accuracy: 0.9951 - val_loss: 0.0218 - val_accuracy: 0.9940
Epoch 5/5
63/63 [==============================] - 6s 90ms/step - loss: 0.0086 - accuracy: 0.9976 - val_loss: 0.0253 - val_accuracy: 0.9932


In [169]:
ncbi_biobert_model.summary()

Model: "model_13"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 attention_mask (InputLayer)    [(None, 180)]        0           []                               
                                                                                                  
 input_ids (InputLayer)         [(None, 180)]        0           []                               
                                                                                                  
 tf_bert_model_13 (TFBertModel)  TFBaseModelOutputWi  108310272  ['attention_mask[0][0]',         
                                thPoolingAndCrossAt               'input_ids[0][0]']              
                                tentions(last_hidde                                               
                                n_state=(None, 180,                                        

In [112]:
# Train with full train/ validation dataset

history = ncbi_biobert_model.fit([biobert_ncbi_train_input_ids, biobert_ncbi_train_attention_mask], 
                                          biobert_ncbi_train_labels, batch_size=8, epochs=3, 
                                          validation_data=([biobert_ncbi_val_input_ids, biobert_ncbi_val_attention_mask], biobert_ncbi_val_labels))


Epoch 1/3
680/680 [==============================] - 46s 67ms/step - loss: 0.0160 - accuracy: 0.9948 - val_loss: 0.0125 - val_accuracy: 0.9962
Epoch 2/3
680/680 [==============================] - 45s 67ms/step - loss: 0.0080 - accuracy: 0.9974 - val_loss: 0.0130 - val_accuracy: 0.9962
Epoch 3/3
680/680 [==============================] - 45s 67ms/step - loss: 0.0042 - accuracy: 0.9986 - val_loss: 0.0150 - val_accuracy: 0.9962


In [113]:
#loss, accuracy = ncbi_biobert_model.evaluate([biobert_ncbi_test_input_ids, biobert_ncbi_test_attention_mask], biobert_ncbi_test_labels, verbose=0)

ncbi_biobert_predictions = ncbi_biobert_model.predict([biobert_ncbi_test_input_ids, biobert_ncbi_test_attention_mask])

30/30 [==============================] - 4s 56ms/step


In [114]:
ncbi_biobert_preds_list = get_argmax_predictions(ncbi_biobert_predictions)

In [115]:
print_classification_report(biobert_ncbi_test_labels, biobert_ncbi_test_attention_mask, ncbi_biobert_preds_list, ncbi_label_list)

  0%|          | 0/941 [00:00<?, ?it/s]

              precision    recall  f1-score   support

     Disease     0.8395    0.8963    0.8670      2294

   micro avg     0.8395    0.8963    0.8670      2294
   macro avg     0.8395    0.8963    0.8670      2294
weighted avg     0.8395    0.8963    0.8670      2294




# BERT+CRF - NCBI

In [ ]:
ncbi_bert_crf_model = create_bert_crf_model(NCBI_NUM_LABELS, NCBI_MAX_LENGTH)

Some layers from the model checkpoint at dslim/bert-large-NER were not used when initializing TFBertModel: ['classifier', 'dropout_73']
- This IS expected if you are initializing TFBertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFBertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
All the layers of TFBertModel were initialized from the model checkpoint at dslim/bert-large-NER.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFBertModel for predictions without further training.


In [ ]:
# Train with sample train/ validation dataset

history = ncbi_bert_crf_model.fit([bert_ncbi_train_input_ids[:100], bert_ncbi_train_attention_mask[:100]], 
                                          bert_ncbi_train_labels[:100], batch_size=8, epochs=5, 
                                          validation_data=([bert_ncbi_val_input_ids[:100], bert_ncbi_val_attention_mask[:100]], bert_ncbi_val_labels[:100]))

Epoch 1/5


13/13 [==============================] - 48s 1s/step - loss: 124.3953 - accuracy: 0.7777 - val_loss_val: 21.5460 - val_val_accuracy: 0.9779
Epoch 2/5
13/13 [==============================] - 7s 527ms/step - loss: 25.1768 - accuracy: 0.9670 - val_loss_val: 14.2454 - val_val_accuracy: 0.9768
Epoch 3/5
13/13 [==============================] - 7s 528ms/step - loss: 14.5345 - accuracy: 0.9720 - val_loss_val: 9.8486 - val_val_accuracy: 0.9813
Epoch 4/5
13/13 [==============================] - 7s 525ms/step - loss: 20.3405 - accuracy: 0.9715 - val_loss_val: 7.6538 - val_val_accuracy: 0.9871
Epoch 5/5
13/13 [==============================] - 7s 523ms/step - loss: 7.4212 - accuracy: 0.9869 - val_loss_val: 6.9995 - val_val_accuracy: 0.9869


In [ ]:
ncbi_bert_crf_model.summary()

Model: "model_with_crf_loss_5"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 model_7 (Functional)        ((None, 180),             333582348 
                              (None, 180, 3),                    
                              (None,),                           
                              (3, 3))                            
                                                                 
Total params: 333,582,352
Trainable params: 333,582,348
Non-trainable params: 4
_________________________________________________________________


In [ ]:
# Train with full train/ validation dataset
history = ncbi_bert_crf_model.fit([bert_ncbi_train_input_ids, bert_ncbi_train_attention_mask], 
                                          bert_ncbi_train_labels, batch_size=8, epochs=5, 
                                          validation_data=([bert_ncbi_val_input_ids, bert_ncbi_val_attention_mask], bert_ncbi_val_labels))


Epoch 1/5
680/680 [==============================] - 267s 392ms/step - loss: 4.3246 - accuracy: 0.9926 - val_loss_val: 3.1554 - val_val_accuracy: 0.9948
Epoch 2/5
680/680 [==============================] - 266s 392ms/step - loss: 1.9906 - accuracy: 0.9967 - val_loss_val: 2.5690 - val_val_accuracy: 0.9959
Epoch 3/5
680/680 [==============================] - 266s 392ms/step - loss: 1.1850 - accuracy: 0.9978 - val_loss_val: 2.6725 - val_val_accuracy: 0.9958
Epoch 4/5
680/680 [==============================] - 269s 395ms/step - loss: 0.7065 - accuracy: 0.9987 - val_loss_val: 2.9343 - val_val_accuracy: 0.9956
Epoch 5/5
680/680 [==============================] - ETA: 0s - loss: 0.5656 - accuracy: 0.9989

In [ ]:
# loss, accuracy = ncbi_bert_crf_model.evaluate([bert_ncbi_test_input_ids, bert_ncbi_test_attention_mask], bert_ncbi_test_labels, verbose=0)

ncbi_bert_crf_predictions = ncbi_bert_crf_model.predict([bert_ncbi_test_input_ids, bert_ncbi_test_attention_mask])

30/30 [==============================] - 6s 196ms/step


In [ ]:
print_classification_report(bert_ncbi_test_labels, bert_ncbi_test_attention_mask, ncbi_bert_crf_predictions, ncbi_label_list)

  0%|          | 0/941 [00:00<?, ?it/s]

              precision    recall  f1-score   support

     Disease     0.8678    0.8577    0.8627      2220

   micro avg     0.8678    0.8577    0.8627      2220
   macro avg     0.8678    0.8577    0.8627      2220
weighted avg     0.8678    0.8577    0.8627      2220



# BERT+LSTM+CRF - NCBI

In [197]:
ncbi_bert_lstm_crf_model = create_bert_lstm_crf_model(NCBI_NUM_LABELS, 16, NCBI_MAX_LENGTH)

Some layers from the model checkpoint at dslim/bert-large-NER were not used when initializing TFBertModel: ['classifier', 'dropout_73']
- This IS expected if you are initializing TFBertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFBertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
All the layers of TFBertModel were initialized from the model checkpoint at dslim/bert-large-NER.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFBertModel for predictions without further training.


In [198]:
# Train with sample train/ validation dataset

history = ncbi_bert_lstm_crf_model.fit([bert_ncbi_train_input_ids[:100], bert_ncbi_train_attention_mask[:100]], 
                                          bert_ncbi_train_labels[:100], batch_size=8, epochs=5, 
                                          validation_data=([bert_ncbi_val_input_ids[:100], bert_ncbi_val_attention_mask[:100]], bert_ncbi_val_labels[:100]))

Epoch 1/5


13/13 [==============================] - 49s 1s/step - loss: 48.4492 - accuracy: 0.9601 - val_loss_val: 20.6425 - val_val_accuracy: 0.9778
Epoch 2/5
13/13 [==============================] - 7s 535ms/step - loss: 27.7096 - accuracy: 0.9661 - val_loss_val: 18.6848 - val_val_accuracy: 0.9778
Epoch 3/5
13/13 [==============================] - 7s 541ms/step - loss: 25.0357 - accuracy: 0.9661 - val_loss_val: 16.9453 - val_val_accuracy: 0.9778
Epoch 4/5
13/13 [==============================] - 7s 531ms/step - loss: 21.7784 - accuracy: 0.9662 - val_loss_val: 14.8489 - val_val_accuracy: 0.9778
Epoch 5/5
13/13 [==============================] - 7s 535ms/step - loss: 17.2509 - accuracy: 0.9683 - val_loss_val: 11.9048 - val_val_accuracy: 0.9797


In [199]:
ncbi_bert_lstm_crf_model.summary()

Model: "model_with_crf_loss_11"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 model_26 (Functional)       ((None, 180),             333645948 
                              (None, 180, 3),                    
                              (None,),                           
                              (3, 3))                            
                                                                 
Total params: 333,645,952
Trainable params: 333,645,948
Non-trainable params: 4
_________________________________________________________________


In [200]:
# Train with full train/ validation dataset

history = ncbi_bert_lstm_crf_model.fit([bert_ncbi_train_input_ids, bert_ncbi_train_attention_mask], 
                                          bert_ncbi_train_labels, batch_size=8, epochs=5, 
                                          validation_data=([bert_ncbi_val_input_ids, bert_ncbi_val_attention_mask], bert_ncbi_val_labels))

Epoch 1/5
680/680 [==============================] - 271s 399ms/step - loss: 6.2075 - accuracy: 0.9909 - val_loss_val: 4.7666 - val_val_accuracy: 0.9945
Epoch 2/5
680/680 [==============================] - 271s 399ms/step - loss: 3.6107 - accuracy: 0.9966 - val_loss_val: 3.7496 - val_val_accuracy: 0.9961
Epoch 3/5
680/680 [==============================] - 271s 399ms/step - loss: 2.7120 - accuracy: 0.9977 - val_loss_val: 3.3736 - val_val_accuracy: 0.9963
Epoch 4/5
680/680 [==============================] - 272s 401ms/step - loss: 2.2661 - accuracy: 0.9981 - val_loss_val: 3.3216 - val_val_accuracy: 0.9964
Epoch 5/5
680/680 [==============================] - 273s 401ms/step - loss: 1.7970 - accuracy: 0.9987 - val_loss_val: 3.5671 - val_val_accuracy: 0.9959


In [201]:
#loss, accuracy = ncbi_bert_bilstm_crf_model.evaluate([bert_ncbi_test_input_ids, bert_ncbi_test_attention_mask], bert_ncbi_test_labels, verbose=0)

ncbi_bert_bilstm_crf_predictions = ncbi_bert_lstm_crf_model.predict([bert_ncbi_test_input_ids, bert_ncbi_test_attention_mask])

30/30 [==============================] - 15s 200ms/step


In [202]:
print_classification_report(bert_ncbi_test_labels, bert_ncbi_test_attention_mask, ncbi_bert_bilstm_crf_predictions, ncbi_label_list)

  0%|          | 0/941 [00:00<?, ?it/s]

              precision    recall  f1-score   support

     Disease     0.8557    0.8973    0.8760      2220

   micro avg     0.8557    0.8973    0.8760      2220
   macro avg     0.8557    0.8973    0.8760      2220
weighted avg     0.8557    0.8973    0.8760      2220



# BERT+BILSTM+CRF - NCBI

In [ ]:
ncbi_bert_bilstm_crf_model = create_bert_bilstm_crf_model(NCBI_NUM_LABELS, 768, NCBI_MAX_LENGTH)

Some layers from the model checkpoint at dslim/bert-large-NER were not used when initializing TFBertModel: ['dropout_73', 'classifier']
- This IS expected if you are initializing TFBertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFBertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
All the layers of TFBertModel were initialized from the model checkpoint at dslim/bert-large-NER.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFBertModel for predictions without further training.


In [ ]:
# Train with sample train/ validation dataset

history = ncbi_bert_bilstm_crf_model.fit([bert_ncbi_train_input_ids[:100], bert_ncbi_train_attention_mask[:100]], 
                                          bert_ncbi_train_labels[:100], batch_size=8, epochs=5, 
                                          validation_data=([bert_ncbi_val_input_ids[:100], bert_ncbi_val_attention_mask[:100]], bert_ncbi_val_labels[:100]))

Epoch 1/5


13/13 [==============================] - 52s 1s/step - loss: 87.2131 - accuracy: 0.8081 - val_loss_val: 21.2740 - val_val_accuracy: 0.9778
Epoch 2/5
13/13 [==============================] - 7s 551ms/step - loss: 26.4480 - accuracy: 0.9661 - val_loss_val: 16.2926 - val_val_accuracy: 0.9778
Epoch 3/5
13/13 [==============================] - 7s 537ms/step - loss: 21.9211 - accuracy: 0.9661 - val_loss_val: 14.6392 - val_val_accuracy: 0.9779
Epoch 4/5
13/13 [==============================] - 7s 533ms/step - loss: 19.5512 - accuracy: 0.9665 - val_loss_val: 13.0484 - val_val_accuracy: 0.9785
Epoch 5/5
13/13 [==============================] - 7s 543ms/step - loss: 16.1269 - accuracy: 0.9691 - val_loss_val: 10.7474 - val_val_accuracy: 0.9791


In [ ]:
ncbi_bert_bilstm_crf_model.summary()

Model: "model_with_crf_loss_6"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 model_8 (Functional)        ((None, 180),             344600076 
                              (None, 180, 3),                    
                              (None,),                           
                              (3, 3))                            
                                                                 
Total params: 344,600,080
Trainable params: 344,600,076
Non-trainable params: 4
_________________________________________________________________


In [ ]:
# Train with full train/ validation dataset

history = ncbi_bert_bilstm_crf_model.fit([bert_ncbi_train_input_ids, bert_ncbi_train_attention_mask], 
                                          bert_ncbi_train_labels, batch_size=8, epochs=5, 
                                          validation_data=([bert_ncbi_val_input_ids, bert_ncbi_val_attention_mask], bert_ncbi_val_labels))

Epoch 1/5
680/680 [==============================] - 273s 401ms/step - loss: 4.9154 - accuracy: 0.9903 - val_loss_val: 3.0598 - val_val_accuracy: 0.9951
Epoch 2/5
680/680 [==============================] - 272s 400ms/step - loss: 1.9652 - accuracy: 0.9965 - val_loss_val: 2.5687 - val_val_accuracy: 0.9956
Epoch 3/5
680/680 [==============================] - 272s 401ms/step - loss: 1.1482 - accuracy: 0.9979 - val_loss_val: 2.3724 - val_val_accuracy: 0.9961
Epoch 4/5
680/680 [==============================] - 271s 399ms/step - loss: 0.7405 - accuracy: 0.9988 - val_loss_val: 2.4904 - val_val_accuracy: 0.9963
Epoch 5/5
680/680 [==============================] - 271s 398ms/step - loss: 0.5797 - accuracy: 0.9990 - val_loss_val: 2.8865 - val_val_accuracy: 0.9962


In [ ]:
#loss, accuracy = ncbi_bert_bilstm_crf_model.evaluate([bert_ncbi_test_input_ids, bert_ncbi_test_attention_mask], bert_ncbi_test_labels, verbose=0)

ncbi_bert_bilstm_crf_predictions = ncbi_bert_bilstm_crf_model.predict([bert_ncbi_test_input_ids, bert_ncbi_test_attention_mask])

30/30 [==============================] - 15s 202ms/step


In [ ]:
print_classification_report(bert_ncbi_test_labels, bert_ncbi_test_attention_mask, ncbi_bert_bilstm_crf_predictions, ncbi_label_list)

  0%|          | 0/941 [00:00<?, ?it/s]

              precision    recall  f1-score   support

     Disease     0.8648    0.8613    0.8630      2220

   micro avg     0.8648    0.8613    0.8630      2220
   macro avg     0.8648    0.8613    0.8630      2220
weighted avg     0.8648    0.8613    0.8630      2220




# BioBERT+CRF - NCBI

In [116]:
ncbi_biobert_crf_model = create_biobert_crf_model(NCBI_NUM_LABELS, NCBI_MAX_LENGTH)

Some weights of the PyTorch model were not used when initializing the TF 2.0 model TFBertModel: ['cls.predictions.transform.dense.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.predictions.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing TFBertModel from a PyTorch model trained on another task or with another architecture (e.g. initializing a TFBertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFBertModel from a PyTorch model that you expect to be exactly identical (e.g. initializing a TFBertForSequenceClassification model from a BertForSequenceClassification model).
All the weights of TFBertModel were initialized from the PyTorch model.
If your task is similar to the task the model of the checkpoint

In [117]:
# Train with sample train/ validation dataset

history = ncbi_biobert_crf_model.fit([biobert_ncbi_train_input_ids[:100], biobert_ncbi_train_attention_mask[:100]], 
                                          biobert_ncbi_train_labels[:100], batch_size=8, epochs=5, 
                                          validation_data=([biobert_ncbi_val_input_ids[:100], biobert_ncbi_val_attention_mask[:100]], biobert_ncbi_val_labels[:100]))

Epoch 1/5


13/13 [==============================] - 30s 764ms/step - loss: 66.8569 - accuracy: 0.9021 - val_loss_val: 24.1733 - val_val_accuracy: 0.9774
Epoch 2/5
13/13 [==============================] - 5s 428ms/step - loss: 33.2328 - accuracy: 0.9651 - val_loss_val: 20.9824 - val_val_accuracy: 0.9778
Epoch 3/5
13/13 [==============================] - 5s 427ms/step - loss: 24.3212 - accuracy: 0.9659 - val_loss_val: 13.6480 - val_val_accuracy: 0.9806
Epoch 4/5
13/13 [==============================] - 5s 422ms/step - loss: 12.5220 - accuracy: 0.9747 - val_loss_val: 8.6588 - val_val_accuracy: 0.9812
Epoch 5/5
13/13 [==============================] - 5s 425ms/step - loss: 7.4729 - accuracy: 0.9831 - val_loss_val: 9.2526 - val_val_accuracy: 0.9838


In [160]:
ncbi_biobert_crf_model.summary()

Model: "model_with_crf_loss_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 model_14 (Functional)       ((None, 180),             108312588 
                              (None, 180, 3),                    
                              (None,),                           
                              (3, 3))                            
                                                                 
Total params: 108,312,592
Trainable params: 108,312,588
Non-trainable params: 4
_________________________________________________________________


In [121]:
# Train with full train/ validation dataset
history = ncbi_biobert_crf_model.fit([biobert_ncbi_train_input_ids, biobert_ncbi_train_attention_mask], 
                                          biobert_ncbi_train_labels, batch_size=8, epochs=2, 
                                          validation_data=([biobert_ncbi_val_input_ids, biobert_ncbi_val_attention_mask], biobert_ncbi_val_labels))


Epoch 1/2
680/680 [==============================] - 216s 317ms/step - loss: 0.7166 - accuracy: 0.9988 - val_loss_val: 3.2286 - val_val_accuracy: 0.9957
Epoch 2/2
680/680 [==============================] - 215s 317ms/step - loss: 0.7902 - accuracy: 0.9987 - val_loss_val: 3.0693 - val_val_accuracy: 0.9960


In [122]:
#loss, accuracy = ncbi_biobert_crf_model.evaluate([biobert_ncbi_test_input_ids, biobert_ncbi_test_attention_mask], biobert_ncbi_test_labels, verbose=0)

ncbi_biobert_crf_predictions = ncbi_biobert_crf_model.predict([biobert_ncbi_test_input_ids, biobert_ncbi_test_attention_mask])

30/30 [==============================] - 3s 115ms/step


In [123]:
print_classification_report(biobert_ncbi_test_labels, biobert_ncbi_test_attention_mask, ncbi_biobert_crf_predictions, ncbi_label_list)

  0%|          | 0/941 [00:00<?, ?it/s]

              precision    recall  f1-score   support

     Disease     0.8539    0.8714    0.8626      2294

   micro avg     0.8539    0.8714    0.8626      2294
   macro avg     0.8539    0.8714    0.8626      2294
weighted avg     0.8539    0.8714    0.8626      2294



# BioBERT+BILSTM+CRF - NCBI

In [269]:
ncbi_biobert_bilstm_crf_model = create_biobert_bilstm_crf_model(NCBI_NUM_LABELS, 700, NCBI_MAX_LENGTH)

Some weights of the PyTorch model were not used when initializing the TF 2.0 model TFBertModel: ['cls.predictions.transform.dense.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.predictions.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing TFBertModel from a PyTorch model trained on another task or with another architecture (e.g. initializing a TFBertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFBertModel from a PyTorch model that you expect to be exactly identical (e.g. initializing a TFBertForSequenceClassification model from a BertForSequenceClassification model).
All the weights of TFBertModel were initialized from the PyTorch model.
If your task is similar to the task the model of the checkpoint

In [263]:
# Train with sample train/ validation dataset
history = ncbi_biobert_bilstm_crf_model.fit([biobert_ncbi_train_input_ids[:100], biobert_ncbi_train_attention_mask[:100]], 
                                          biobert_ncbi_train_labels[:100], batch_size=8, epochs=5, 
                                          validation_data=([biobert_ncbi_val_input_ids[:100], biobert_ncbi_val_attention_mask[:100]], biobert_ncbi_val_labels[:100]))

Epoch 1/5


13/13 [==============================] - 31s 858ms/step - loss: 40.7324 - accuracy: 0.9018 - val_loss_val: 16.9787 - val_val_accuracy: 0.9778
Epoch 2/5
13/13 [==============================] - 6s 463ms/step - loss: 20.0226 - accuracy: 0.9653 - val_loss_val: 10.5976 - val_val_accuracy: 0.9779
Epoch 3/5
13/13 [==============================] - 6s 467ms/step - loss: 13.2146 - accuracy: 0.9686 - val_loss_val: 11.2075 - val_val_accuracy: 0.9778
Epoch 4/5
13/13 [==============================] - 6s 461ms/step - loss: 11.0439 - accuracy: 0.9727 - val_loss_val: 6.6294 - val_val_accuracy: 0.9858
Epoch 5/5
13/13 [==============================] - 6s 457ms/step - loss: 7.1078 - accuracy: 0.9846 - val_loss_val: 5.9625 - val_val_accuracy: 0.9853


In [270]:
# Train with sample train/ validation dataset
history = ncbi_biobert_bilstm_crf_model.fit([biobert_ncbi_train_input_ids[:100], biobert_ncbi_train_attention_mask[:100]], 
                                          biobert_ncbi_train_labels[:100], batch_size=8, epochs=5, 
                                          validation_data=([biobert_ncbi_val_input_ids[:100], biobert_ncbi_val_attention_mask[:100]], biobert_ncbi_val_labels[:100]))

Epoch 1/5


13/13 [==============================] - 32s 844ms/step - loss: 82.4589 - accuracy: 0.8520 - val_loss_val: 22.3933 - val_val_accuracy: 0.9778
Epoch 2/5
13/13 [==============================] - 6s 460ms/step - loss: 32.1567 - accuracy: 0.9651 - val_loss_val: 18.3432 - val_val_accuracy: 0.9778
Epoch 3/5
13/13 [==============================] - 6s 465ms/step - loss: 26.0286 - accuracy: 0.9636 - val_loss_val: 17.5906 - val_val_accuracy: 0.9748
Epoch 4/5
13/13 [==============================] - 6s 463ms/step - loss: 20.5581 - accuracy: 0.9647 - val_loss_val: 13.0399 - val_val_accuracy: 0.9782
Epoch 5/5
13/13 [==============================] - 6s 456ms/step - loss: 15.6629 - accuracy: 0.9689 - val_loss_val: 10.7891 - val_val_accuracy: 0.9823


In [247]:
ncbi_biobert_bilstm_crf_model.summary()

Model: "model_with_crf_loss_20"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 model_36 (Functional)       ((None, 180),             113560332 
                              (None, 180, 3),                    
                              (None,),                           
                              (3, 3))                            
                                                                 
Total params: 113,560,336
Trainable params: 113,560,332
Non-trainable params: 4
_________________________________________________________________


In [271]:
# Train with full train/ validation dataset
history = ncbi_biobert_bilstm_crf_model.fit([biobert_ncbi_train_input_ids, biobert_ncbi_train_attention_mask], 
                                          biobert_ncbi_train_labels, batch_size=8, epochs=5, 
                                          validation_data=([biobert_ncbi_val_input_ids, biobert_ncbi_val_attention_mask], biobert_ncbi_val_labels))


Epoch 1/5
680/680 [==============================] - 231s 340ms/step - loss: 5.7419 - accuracy: 0.9899 - val_loss_val: 3.5042 - val_val_accuracy: 0.9944
Epoch 2/5
680/680 [==============================] - 232s 341ms/step - loss: 2.1984 - accuracy: 0.9965 - val_loss_val: 3.0624 - val_val_accuracy: 0.9957
Epoch 3/5
680/680 [==============================] - 232s 341ms/step - loss: 1.3319 - accuracy: 0.9980 - val_loss_val: 3.4049 - val_val_accuracy: 0.9958
Epoch 4/5
680/680 [==============================] - 230s 339ms/step - loss: 1.0080 - accuracy: 0.9985 - val_loss_val: 3.7445 - val_val_accuracy: 0.9954
Epoch 5/5
680/680 [==============================] - 229s 337ms/step - loss: 0.9083 - accuracy: 0.9986 - val_loss_val: 4.9652 - val_val_accuracy: 0.9947


In [272]:
# loss, accuracy = ncbi_biobert_bilstm_crf_model.evaluate([biobert_ncbi_test_input_ids, biobert_ncbi_test_attention_mask], biobert_ncbi_test_labels, verbose=0)

ncbi_biobert_bilstm_crf_predictions = ncbi_biobert_bilstm_crf_model.predict([biobert_ncbi_test_input_ids, biobert_ncbi_test_attention_mask])

30/30 [==============================] - 8s 127ms/step


In [273]:
print_classification_report(biobert_ncbi_test_labels, biobert_ncbi_test_attention_mask, ncbi_biobert_bilstm_crf_predictions, ncbi_label_list)

  0%|          | 0/941 [00:00<?, ?it/s]

              precision    recall  f1-score   support

     Disease     0.8081    0.9159    0.8586      2294

   micro avg     0.8081    0.9159    0.8586      2294
   macro avg     0.8081    0.9159    0.8586      2294
weighted avg     0.8081    0.9159    0.8586      2294



# BERT - GM

In [ ]:
gm_bert_model = create_bert_model(GM_NUM_LABELS, GM_MAX_LENGTH)

Some layers from the model checkpoint at dslim/bert-large-NER were not used when initializing TFBertModel: ['classifier', 'dropout_73']
- This IS expected if you are initializing TFBertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFBertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
All the layers of TFBertModel were initialized from the model checkpoint at dslim/bert-large-NER.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFBertModel for predictions without further training.


In [ ]:
# Train with sample train/ validation dataset
history = gm_bert_model.fit([bert_gm_train_input_ids[:100], bert_gm_train_attention_mask[:100]], 
                                          bert_gm_train_labels[:100], batch_size=8, epochs=5, 
                                          validation_data=([bert_gm_val_input_ids[:100], bert_gm_val_attention_mask[:100]], bert_gm_val_labels[:100]))

Epoch 1/5


13/13 [==============================] - 41s 874ms/step - loss: 0.0887 - accuracy: 0.9876 - val_loss: 0.0450 - val_accuracy: 0.9947
Epoch 2/5
13/13 [==============================] - 4s 298ms/step - loss: 0.0584 - accuracy: 0.9919 - val_loss: 0.0317 - val_accuracy: 0.9947
Epoch 3/5
13/13 [==============================] - 4s 297ms/step - loss: 0.0475 - accuracy: 0.9920 - val_loss: 0.0239 - val_accuracy: 0.9947
Epoch 4/5
13/13 [==============================] - 4s 296ms/step - loss: 0.0396 - accuracy: 0.9896 - val_loss: 0.0189 - val_accuracy: 0.9950
Epoch 5/5
13/13 [==============================] - 4s 297ms/step - loss: 0.0284 - accuracy: 0.9919 - val_loss: 0.0175 - val_accuracy: 0.9949


In [ ]:
# Train with full train/ validation dataset

history = gm_bert_model.fit([bert_gm_train_input_ids, bert_gm_train_attention_mask], 
                                          bert_gm_train_labels, batch_size=8, epochs=3, 
                                          validation_data=([bert_gm_val_input_ids, bert_gm_val_attention_mask], bert_gm_val_labels))


Epoch 1/2
1563/1563 [==============================] - 357s 229ms/step - loss: 0.0207 - accuracy: 0.9926 - val_loss: 0.0139 - val_accuracy: 0.9949
Epoch 2/2
1563/1563 [==============================] - 357s 228ms/step - loss: 0.0107 - accuracy: 0.9962 - val_loss: 0.0130 - val_accuracy: 0.9956


In [ ]:
#loss, accuracy = gm_bert_model.evaluate([bert_gm_test_input_ids, bert_gm_test_attention_mask], bert_gm_test_labels, verbose=0)

bert_gm_predictions = gm_bert_model.predict([bert_gm_test_input_ids, bert_gm_test_attention_mask])

157/157 [==============================] - 42s 229ms/step


In [ ]:
bert_gm_preds_list = get_argmax_predictions(bert_gm_predictions)

In [ ]:
print_classification_report(bert_gm_test_labels, bert_gm_test_attention_mask, bert_gm_preds_list, gm_label_list)

  0%|          | 0/5001 [00:00<?, ?it/s]

              precision    recall  f1-score   support

     Disease     0.8269    0.8565    0.8415     16110

   micro avg     0.8269    0.8565    0.8415     16110
   macro avg     0.8269    0.8565    0.8415     16110
weighted avg     0.8269    0.8565    0.8415     16110



# BioBERT - GM

In [143]:
gm_biobert_model = create_biobert_model(GM_NUM_LABELS, GM_MAX_LENGTH)

Some weights of the PyTorch model were not used when initializing the TF 2.0 model TFBertModel: ['cls.predictions.transform.dense.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.predictions.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing TFBertModel from a PyTorch model trained on another task or with another architecture (e.g. initializing a TFBertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFBertModel from a PyTorch model that you expect to be exactly identical (e.g. initializing a TFBertForSequenceClassification model from a BertForSequenceClassification model).
All the weights of TFBertModel were initialized from the PyTorch model.
If your task is similar to the task the model of the checkpoint

In [144]:
# Train with sample train/ validation dataset

history = gm_biobert_model.fit([biobert_gm_train_input_ids[:100], biobert_gm_train_attention_mask[:100]], 
                                          biobert_gm_train_labels[:100], batch_size=8, epochs=5, 
                                          validation_data=([biobert_gm_val_input_ids[:100], biobert_gm_val_attention_mask[:100]], biobert_gm_val_labels[:100]))


Epoch 1/5


13/13 [==============================] - 22s 380ms/step - loss: 0.1973 - accuracy: 0.9346 - val_loss: 0.0555 - val_accuracy: 0.9946
Epoch 2/5
13/13 [==============================] - 2s 127ms/step - loss: 0.0625 - accuracy: 0.9918 - val_loss: 0.0398 - val_accuracy: 0.9946
Epoch 3/5
13/13 [==============================] - 2s 126ms/step - loss: 0.0516 - accuracy: 0.9920 - val_loss: 0.0343 - val_accuracy: 0.9946
Epoch 4/5
13/13 [==============================] - 2s 127ms/step - loss: 0.0452 - accuracy: 0.9919 - val_loss: 0.0279 - val_accuracy: 0.9946
Epoch 5/5
13/13 [==============================] - 2s 127ms/step - loss: 0.0323 - accuracy: 0.9921 - val_loss: 0.0216 - val_accuracy: 0.9946


In [145]:
# Train with full train/ validation dataset

history = gm_biobert_model.fit([biobert_gm_train_input_ids, biobert_gm_train_attention_mask], 
                                          biobert_gm_train_labels, batch_size=8, epochs=3, 
                                          validation_data=([biobert_gm_val_input_ids, biobert_gm_val_attention_mask], biobert_gm_val_labels))


Epoch 1/3
1563/1563 [==============================] - 147s 94ms/step - loss: 0.0190 - accuracy: 0.9932 - val_loss: 0.0133 - val_accuracy: 0.9952
Epoch 2/3
1563/1563 [==============================] - 148s 95ms/step - loss: 0.0093 - accuracy: 0.9967 - val_loss: 0.0133 - val_accuracy: 0.9954
Epoch 3/3
1563/1563 [==============================] - 148s 94ms/step - loss: 0.0070 - accuracy: 0.9976 - val_loss: 0.0125 - val_accuracy: 0.9958


In [146]:
#loss, accuracy = gm_biobert_model.evaluate([biobert_gm_test_input_ids, biobert_gm_test_attention_mask], biobert_gm_test_labels, verbose=0)

gm_biobert_predictions = gm_biobert_model.predict([biobert_gm_test_input_ids, biobert_gm_test_attention_mask])

157/157 [==============================] - 17s 90ms/step


In [147]:
biobert_gm_preds_list = get_argmax_predictions(gm_biobert_predictions)

In [148]:
print_classification_report(biobert_gm_test_labels, biobert_gm_test_attention_mask, biobert_gm_preds_list, gm_label_list)

  0%|          | 0/5001 [00:00<?, ?it/s]

              precision    recall  f1-score   support

        GENE     0.8364    0.8724    0.8540     16054

   micro avg     0.8364    0.8724    0.8540     16054
   macro avg     0.8364    0.8724    0.8540     16054
weighted avg     0.8364    0.8724    0.8540     16054




# BERT+CRF - GM

In [ ]:
gm_bert_crf_model = create_bert_crf_model(GM_NUM_LABELS, GM_MAX_LENGTH)

Some layers from the model checkpoint at dslim/bert-large-NER were not used when initializing TFBertModel: ['classifier', 'dropout_73']
- This IS expected if you are initializing TFBertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFBertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
All the layers of TFBertModel were initialized from the model checkpoint at dslim/bert-large-NER.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFBertModel for predictions without further training.


In [ ]:
# Train with sample train/ validation dataset

history = gm_bert_crf_model.fit([bert_gm_train_input_ids[:100], bert_gm_train_attention_mask[:100]], 
                                          bert_gm_train_labels[:100], batch_size=8, epochs=5, 
                                          validation_data=([bert_gm_val_input_ids[:100], bert_gm_val_attention_mask[:100]], bert_gm_val_labels[:100]))


Epoch 1/5


13/13 [==============================] - 54s 1s/step - loss: 24.5041 - accuracy: 0.9875 - val_loss_val: 11.1862 - val_val_accuracy: 0.9947
Epoch 2/5
13/13 [==============================] - 11s 837ms/step - loss: 13.8278 - accuracy: 0.9919 - val_loss_val: 6.9680 - val_val_accuracy: 0.9946
Epoch 3/5
13/13 [==============================] - 11s 834ms/step - loss: 7.9246 - accuracy: 0.9918 - val_loss_val: 5.4242 - val_val_accuracy: 0.9947
Epoch 4/5
13/13 [==============================] - 11s 841ms/step - loss: 5.7719 - accuracy: 0.9935 - val_loss_val: 4.6876 - val_val_accuracy: 0.9947
Epoch 5/5
13/13 [==============================] - 11s 832ms/step - loss: 3.9498 - accuracy: 0.9950 - val_loss_val: 4.3821 - val_val_accuracy: 0.9949


In [ ]:
# Train with full train/ validation dataset

history = gm_bert_crf_model.fit([bert_gm_train_input_ids, bert_gm_train_attention_mask], 
                                          bert_gm_train_labels, batch_size=8, epochs=3, 
                                          validation_data=([bert_gm_val_input_ids, bert_gm_val_attention_mask], bert_gm_val_labels))


Epoch 1/3
1563/1563 [==============================] - 980s 627ms/step - loss: 4.9994 - accuracy: 0.9931 - val_loss_val: 4.4612 - val_val_accuracy: 0.9939
Epoch 2/3
1563/1563 [==============================] - 978s 626ms/step - loss: 2.7999 - accuracy: 0.9963 - val_loss_val: 3.3340 - val_val_accuracy: 0.9953
Epoch 3/3
1563/1563 [==============================] - 978s 626ms/step - loss: 1.6458 - accuracy: 0.9977 - val_loss_val: 3.5819 - val_val_accuracy: 0.9956


In [ ]:
#loss, accuracy = gm_bert_crf_model.evaluate([bert_gm_test_input_ids, bert_gm_test_attention_mask], bert_gm_test_labels, verbose=0)

bert_crf_gm_predictions = gm_bert_crf_model.predict([bert_gm_test_input_ids, bert_gm_test_attention_mask])

157/157 [==============================] - 58s 327ms/step


In [ ]:
print_classification_report(bert_gm_test_labels, bert_gm_test_attention_mask, bert_crf_gm_predictions, gm_label_list)

  0%|          | 0/5001 [00:00<?, ?it/s]

              precision    recall  f1-score   support

     Disease     0.8535    0.8644    0.8589     16110

   micro avg     0.8535    0.8644    0.8589     16110
   macro avg     0.8535    0.8644    0.8589     16110
weighted avg     0.8535    0.8644    0.8589     16110



# BERT+BILSTM+CRF - GM

In [ ]:
gm_bert_bilstm_crf_model = create_bert_bilstm_crf_model(GM_NUM_LABELS, 768, GM_MAX_LENGTH)

Some layers from the model checkpoint at dslim/bert-large-NER were not used when initializing TFBertModel: ['classifier', 'dropout_73']
- This IS expected if you are initializing TFBertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFBertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
All the layers of TFBertModel were initialized from the model checkpoint at dslim/bert-large-NER.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFBertModel for predictions without further training.


In [ ]:
# Train with sample train/ validation dataset

history = gm_bert_bilstm_crf_model.fit([bert_gm_train_input_ids[:100], bert_gm_train_attention_mask[:100]], 
                                          bert_gm_train_labels[:100], batch_size=8, epochs=5, 
                                          validation_data=([bert_gm_val_input_ids[:100], bert_gm_val_attention_mask[:100]], bert_gm_val_labels[:100]))


Epoch 1/5


13/13 [==============================] - 58s 2s/step - loss: 36.1611 - accuracy: 0.9824 - val_loss_val: 9.8290 - val_val_accuracy: 0.9947
Epoch 2/5
13/13 [==============================] - 11s 884ms/step - loss: 13.5605 - accuracy: 0.9919 - val_loss_val: 8.5107 - val_val_accuracy: 0.9947
Epoch 3/5
13/13 [==============================] - 11s 881ms/step - loss: 10.5892 - accuracy: 0.9919 - val_loss_val: 7.4262 - val_val_accuracy: 0.9947
Epoch 4/5
13/13 [==============================] - 11s 861ms/step - loss: 9.6227 - accuracy: 0.9919 - val_loss_val: 10.5341 - val_val_accuracy: 0.9872
Epoch 5/5
13/13 [==============================] - 11s 873ms/step - loss: 12.9339 - accuracy: 0.9847 - val_loss_val: 6.9933 - val_val_accuracy: 0.9947


In [ ]:
# Train with full train/ validation dataset

history = gm_bert_bilstm_crf_model.fit([bert_gm_train_input_ids, bert_gm_train_attention_mask], 
                                          bert_gm_train_labels, batch_size=8, epochs=3, 
                                          validation_data=([bert_gm_val_input_ids, bert_gm_val_attention_mask], bert_gm_val_labels))


Epoch 1/3
1563/1563 [==============================] - 1033s 661ms/step - loss: 5.9637 - accuracy: 0.9918 - val_loss_val: 4.2681 - val_val_accuracy: 0.9937
Epoch 2/3
1563/1563 [==============================] - 1031s 660ms/step - loss: 2.9635 - accuracy: 0.9957 - val_loss_val: 3.2598 - val_val_accuracy: 0.9951
Epoch 3/3
1563/1563 [==============================] - 1031s 660ms/step - loss: 1.9458 - accuracy: 0.9972 - val_loss_val: 3.4036 - val_val_accuracy: 0.9954


In [ ]:
#loss, accuracy = gm_bert_bilstm_crf_model.evaluate([bert_gm_test_input_ids, bert_gm_test_attention_mask], bert_gm_test_labels, verbose=0)

gm_bert_bilstm_crf_predictions = gm_bert_bilstm_crf_model.predict([bert_gm_test_input_ids, bert_gm_test_attention_mask])

157/157 [==============================] - 60s 341ms/step


In [ ]:
print_classification_report(bert_gm_test_labels, bert_gm_test_attention_mask, gm_bert_bilstm_crf_predictions, gm_label_list)

  0%|          | 0/5001 [00:00<?, ?it/s]

              precision    recall  f1-score   support

     Disease     0.8129    0.8815    0.8458     16110

   micro avg     0.8129    0.8815    0.8458     16110
   macro avg     0.8129    0.8815    0.8458     16110
weighted avg     0.8129    0.8815    0.8458     16110




# BioBERT+CRF - GM

In [149]:
gm_biobert_crf_model = create_biobert_crf_model(GM_NUM_LABELS, GM_MAX_LENGTH)

Some weights of the PyTorch model were not used when initializing the TF 2.0 model TFBertModel: ['cls.predictions.transform.dense.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.predictions.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing TFBertModel from a PyTorch model trained on another task or with another architecture (e.g. initializing a TFBertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFBertModel from a PyTorch model that you expect to be exactly identical (e.g. initializing a TFBertForSequenceClassification model from a BertForSequenceClassification model).
All the weights of TFBertModel were initialized from the PyTorch model.
If your task is similar to the task the model of the checkpoint

In [150]:
# Train with sample train/ validation dataset

history = gm_biobert_crf_model.fit([biobert_gm_train_input_ids[:100], biobert_gm_train_attention_mask[:100]], 
                                          biobert_gm_train_labels[:100], batch_size=8, epochs=5, 
                                          validation_data=([biobert_gm_val_input_ids[:100], biobert_gm_val_attention_mask[:100]], biobert_gm_val_labels[:100]))


Epoch 1/5


13/13 [==============================] - 31s 980ms/step - loss: 89.3413 - accuracy: 0.9175 - val_loss_val: 16.6550 - val_val_accuracy: 0.9946
Epoch 2/5
13/13 [==============================] - 9s 669ms/step - loss: 19.4220 - accuracy: 0.9920 - val_loss_val: 15.1148 - val_val_accuracy: 0.9946
Epoch 3/5
13/13 [==============================] - 9s 676ms/step - loss: 18.5760 - accuracy: 0.9920 - val_loss_val: 13.5913 - val_val_accuracy: 0.9946
Epoch 4/5
13/13 [==============================] - 8s 665ms/step - loss: 15.7491 - accuracy: 0.9920 - val_loss_val: 12.4724 - val_val_accuracy: 0.9946
Epoch 5/5
13/13 [==============================] - 8s 658ms/step - loss: 14.9561 - accuracy: 0.9920 - val_loss_val: 12.1526 - val_val_accuracy: 0.9946


In [151]:
# Train with full train/ validation dataset

history = gm_biobert_crf_model.fit([biobert_gm_train_input_ids, biobert_gm_train_attention_mask], 
                                          biobert_gm_train_labels, batch_size=8, epochs=3, 
                                          validation_data=([biobert_gm_val_input_ids, biobert_gm_val_attention_mask], biobert_gm_val_labels))


Epoch 1/3
1563/1563 [==============================] - 778s 498ms/step - loss: 6.7130 - accuracy: 0.9927 - val_loss_val: 4.7303 - val_val_accuracy: 0.9946
Epoch 2/3
1563/1563 [==============================] - 777s 497ms/step - loss: 3.1837 - accuracy: 0.9964 - val_loss_val: 4.2048 - val_val_accuracy: 0.9957
Epoch 3/3
1563/1563 [==============================] - 778s 498ms/step - loss: 2.1381 - accuracy: 0.9976 - val_loss_val: 4.7540 - val_val_accuracy: 0.9957


In [152]:
#loss, accuracy = gm_biobert_crf_model.evaluate([biobert_gm_test_input_ids, biobert_gm_test_attention_mask], biobert_gm_test_labels, verbose=0)

gm_biobert_crf_predictions = gm_biobert_crf_model.predict([biobert_gm_test_input_ids, biobert_gm_test_attention_mask])

157/157 [==============================] - 33s 189ms/step


In [153]:
print_classification_report(biobert_gm_test_labels, biobert_gm_test_attention_mask, gm_biobert_crf_predictions, gm_label_list)

  0%|          | 0/5001 [00:00<?, ?it/s]

              precision    recall  f1-score   support

        GENE     0.8376    0.8647    0.8510     16054

   micro avg     0.8376    0.8647    0.8510     16054
   macro avg     0.8376    0.8647    0.8510     16054
weighted avg     0.8376    0.8647    0.8510     16054



# BioBERT+BILSTM+CRF - GM

In [162]:
gm_biobert_bilstm_crf_model = create_biobert_bilstm_crf_model(GM_NUM_LABELS, 768, GM_MAX_LENGTH)

Some weights of the PyTorch model were not used when initializing the TF 2.0 model TFBertModel: ['cls.predictions.transform.dense.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.predictions.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing TFBertModel from a PyTorch model trained on another task or with another architecture (e.g. initializing a TFBertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFBertModel from a PyTorch model that you expect to be exactly identical (e.g. initializing a TFBertForSequenceClassification model from a BertForSequenceClassification model).
All the weights of TFBertModel were initialized from the PyTorch model.
If your task is similar to the task the model of the checkpoint

In [163]:
# Train with sample train/ validation dataset

history = gm_biobert_bilstm_crf_model.fit([biobert_gm_train_input_ids[:100], biobert_gm_train_attention_mask[:100]], 
                                          biobert_gm_train_labels[:100], batch_size=8, epochs=5, 
                                          validation_data=([biobert_gm_val_input_ids[:100], biobert_gm_val_attention_mask[:100]], biobert_gm_val_labels[:100]))

Epoch 1/5


13/13 [==============================] - 35s 1s/step - loss: 63.2327 - accuracy: 0.9393 - val_loss_val: 14.9559 - val_val_accuracy: 0.9946
Epoch 2/5
13/13 [==============================] - 9s 708ms/step - loss: 16.7575 - accuracy: 0.9920 - val_loss_val: 13.4261 - val_val_accuracy: 0.9946
Epoch 3/5
13/13 [==============================] - 9s 699ms/step - loss: 14.7772 - accuracy: 0.9920 - val_loss_val: 11.6792 - val_val_accuracy: 0.9946
Epoch 4/5
13/13 [==============================] - 9s 710ms/step - loss: 11.4607 - accuracy: 0.9921 - val_loss_val: 11.6211 - val_val_accuracy: 0.9946
Epoch 5/5
13/13 [==============================] - 9s 706ms/step - loss: 8.4271 - accuracy: 0.9925 - val_loss_val: 11.8558 - val_val_accuracy: 0.9946


In [164]:
# Train with full train/ validation dataset

history = gm_biobert_bilstm_crf_model.fit([biobert_gm_train_input_ids, biobert_gm_train_attention_mask], 
                                          biobert_gm_train_labels, batch_size=8, epochs=3, 
                                          validation_data=([biobert_gm_val_input_ids, biobert_gm_val_attention_mask], biobert_gm_val_labels))


Epoch 1/3
1563/1563 [==============================] - 826s 529ms/step - loss: 7.8278 - accuracy: 0.9919 - val_loss_val: 4.9613 - val_val_accuracy: 0.9948
Epoch 2/3
1563/1563 [==============================] - 822s 526ms/step - loss: 3.8112 - accuracy: 0.9961 - val_loss_val: 4.9124 - val_val_accuracy: 0.9953
Epoch 3/3
1563/1563 [==============================] - 819s 524ms/step - loss: 3.0736 - accuracy: 0.9971 - val_loss_val: 4.9255 - val_val_accuracy: 0.9954


In [165]:
#loss, accuracy = gm_biobert_bilstm_crf_model.evaluate([biobert_gm_test_input_ids, biobert_gm_test_attention_mask], biobert_gm_test_labels, verbose=0)

gm_biobert_bilstm_crf_predictions = gm_biobert_bilstm_crf_model.predict([biobert_gm_test_input_ids, biobert_gm_test_attention_mask])

157/157 [==============================] - 36s 204ms/step


In [166]:
print_classification_report(biobert_gm_test_labels, biobert_gm_test_attention_mask, gm_biobert_bilstm_crf_predictions, gm_label_list)

  0%|          | 0/5001 [00:00<?, ?it/s]

              precision    recall  f1-score   support

        GENE     0.8128    0.8247    0.8187     16054

   micro avg     0.8128    0.8247    0.8187     16054
   macro avg     0.8128    0.8247    0.8187     16054
weighted avg     0.8128    0.8247    0.8187     16054



# BERT - CDR

In [ ]:
cdr_bert_model = create_bert_model(CDR_NUM_LABELS, CDR_MAX_LENGTH)

Some layers from the model checkpoint at dslim/bert-large-NER were not used when initializing TFBertModel: ['classifier', 'dropout_73']
- This IS expected if you are initializing TFBertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFBertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
All the layers of TFBertModel were initialized from the model checkpoint at dslim/bert-large-NER.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFBertModel for predictions without further training.


In [ ]:
# Train with sample train/ validation dataset
history = cdr_bert_model.fit([bert_cdr_train_input_ids[:100], bert_cdr_train_attention_mask[:100]], 
                                          bert_cdr_train_labels[:100], batch_size=8, epochs=5, 
                                          validation_data=([bert_cdr_val_input_ids[:100], bert_cdr_val_attention_mask[:100]], bert_cdr_val_labels[:100]))


Epoch 1/5


/usr/local/lib/python3.8/dist-packages/tensorflow/python/util/dispatch.py:1082: UserWarning: "`sparse_categorical_crossentropy` received `from_logits=True`, but the `output` argument was produced by a sigmoid or softmax activation and thus does not represent logits. Was this intended?"
  return dispatch_target(*args, **kwargs)


13/13 [==============================] - 40s 751ms/step - loss: 0.5054 - accuracy: 0.8520 - val_loss: 0.2041 - val_accuracy: 0.9727
Epoch 2/5
13/13 [==============================] - 4s 288ms/step - loss: 0.1896 - accuracy: 0.9682 - val_loss: 0.1179 - val_accuracy: 0.9719
Epoch 3/5
13/13 [==============================] - 4s 284ms/step - loss: 0.1139 - accuracy: 0.9695 - val_loss: 0.0661 - val_accuracy: 0.9759
Epoch 4/5
13/13 [==============================] - 4s 287ms/step - loss: 0.0773 - accuracy: 0.9747 - val_loss: 0.0577 - val_accuracy: 0.9788
Epoch 5/5
13/13 [==============================] - 4s 287ms/step - loss: 0.0583 - accuracy: 0.9812 - val_loss: 0.0532 - val_accuracy: 0.9800


In [ ]:
# Train with full train/ validation dataset

history = cdr_bert_model.fit([bert_cdr_train_input_ids, bert_cdr_train_attention_mask], 
                                          bert_cdr_train_labels, batch_size=8, epochs=3, 
                                          validation_data=([bert_cdr_val_input_ids, bert_cdr_val_attention_mask], bert_cdr_val_labels))


Epoch 1/3
571/571 [==============================] - 163s 285ms/step - loss: 0.0343 - accuracy: 0.9898 - val_loss: 0.0229 - val_accuracy: 0.9938
Epoch 2/3
571/571 [==============================] - 163s 286ms/step - loss: 0.0200 - accuracy: 0.9949 - val_loss: 0.0204 - val_accuracy: 0.9946
Epoch 3/3
571/571 [==============================] - 163s 285ms/step - loss: 0.0151 - accuracy: 0.9964 - val_loss: 0.0207 - val_accuracy: 0.9947


In [ ]:
#loss, accuracy = cdr_bert_model.evaluate([bert_cdr_test_input_ids, bert_cdr_test_attention_mask], bert_cdr_test_labels, verbose=0)

cdr_bert_predictions = cdr_bert_model.predict([bert_cdr_test_input_ids, bert_cdr_test_attention_mask])

150/150 [==============================] - 33s 221ms/step


In [ ]:
cdr_bert_pred_list = get_argmax_predictions(cdr_bert_predictions)

In [ ]:
print_classification_report(bert_cdr_test_labels, bert_cdr_test_attention_mask, cdr_bert_pred_list, cdr_label_list)

  0%|          | 0/4798 [00:00<?, ?it/s]

              precision    recall  f1-score   support

    Chemical     0.9300    0.9209    0.9254     17587
     Disease     0.8066    0.8485    0.8270     12301

   micro avg     0.8774    0.8911    0.8842     29888
   macro avg     0.8683    0.8847    0.8762     29888
weighted avg     0.8792    0.8911    0.8849     29888



# BioBERT - CDR

In [176]:
cdr_biobert_model = create_biobert_model(CDR_NUM_LABELS, CDR_MAX_LENGTH)

Some weights of the PyTorch model were not used when initializing the TF 2.0 model TFBertModel: ['cls.predictions.transform.dense.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.predictions.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing TFBertModel from a PyTorch model trained on another task or with another architecture (e.g. initializing a TFBertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFBertModel from a PyTorch model that you expect to be exactly identical (e.g. initializing a TFBertForSequenceClassification model from a BertForSequenceClassification model).
All the weights of TFBertModel were initialized from the PyTorch model.
If your task is similar to the task the model of the checkpoint

In [177]:
# Train with sample train/ validation dataset

history = cdr_biobert_model.fit([biobert_cdr_train_input_ids[:100], biobert_cdr_train_attention_mask[:100]], 
                                          biobert_cdr_train_labels[:100], batch_size=8, epochs=5, 
                                          validation_data=([biobert_cdr_val_input_ids[:100], biobert_cdr_val_attention_mask[:100]], biobert_cdr_val_labels[:100]))


Epoch 1/5


/usr/local/lib/python3.8/dist-packages/tensorflow/python/util/dispatch.py:1082: UserWarning: "`sparse_categorical_crossentropy` received `from_logits=True`, but the `output` argument was produced by a sigmoid or softmax activation and thus does not represent logits. Was this intended?"
  return dispatch_target(*args, **kwargs)


13/13 [==============================] - 19s 361ms/step - loss: 0.4649 - accuracy: 0.8831 - val_loss: 0.1286 - val_accuracy: 0.9758
Epoch 2/5
13/13 [==============================] - 2s 124ms/step - loss: 0.1548 - accuracy: 0.9677 - val_loss: 0.0831 - val_accuracy: 0.9760
Epoch 3/5
13/13 [==============================] - 2s 124ms/step - loss: 0.0844 - accuracy: 0.9748 - val_loss: 0.0523 - val_accuracy: 0.9816
Epoch 4/5
13/13 [==============================] - 2s 125ms/step - loss: 0.0497 - accuracy: 0.9837 - val_loss: 0.0418 - val_accuracy: 0.9855
Epoch 5/5
13/13 [==============================] - 2s 126ms/step - loss: 0.0379 - accuracy: 0.9879 - val_loss: 0.0429 - val_accuracy: 0.9849


In [178]:
# Train with full train/ validation dataset

history = cdr_biobert_model.fit([biobert_cdr_train_input_ids, biobert_cdr_train_attention_mask], 
                                          biobert_cdr_train_labels, batch_size=8, epochs=5, 
                                          validation_data=([biobert_cdr_val_input_ids, biobert_cdr_val_attention_mask], biobert_cdr_val_labels))


Epoch 1/5
571/571 [==============================] - 69s 122ms/step - loss: 0.0241 - accuracy: 0.9921 - val_loss: 0.0170 - val_accuracy: 0.9945
Epoch 2/5
571/571 [==============================] - 69s 121ms/step - loss: 0.0094 - accuracy: 0.9970 - val_loss: 0.0169 - val_accuracy: 0.9947
Epoch 3/5
571/571 [==============================] - 70s 122ms/step - loss: 0.0051 - accuracy: 0.9984 - val_loss: 0.0191 - val_accuracy: 0.9949
Epoch 4/5
571/571 [==============================] - 69s 122ms/step - loss: 0.0035 - accuracy: 0.9989 - val_loss: 0.0214 - val_accuracy: 0.9951
Epoch 5/5
571/571 [==============================] - 69s 122ms/step - loss: 0.0027 - accuracy: 0.9992 - val_loss: 0.0239 - val_accuracy: 0.9951


In [179]:
#loss, accuracy = cdr_biobert_model.evaluate([biobert_cdr_test_input_ids, biobert_cdr_test_attention_mask], biobert_cdr_test_labels, verbose=0)

cdr_biobert_predictions = cdr_biobert_model.predict([biobert_cdr_test_input_ids, biobert_cdr_test_attention_mask])

150/150 [==============================] - 16s 88ms/step


In [180]:
cdr_biobert_pred_list = get_argmax_predictions(cdr_biobert_predictions)

In [181]:
print_classification_report(biobert_cdr_test_labels, biobert_cdr_test_attention_mask, cdr_biobert_pred_list, cdr_label_list)

  0%|          | 0/4798 [00:00<?, ?it/s]

              precision    recall  f1-score   support

    Chemical     0.9231    0.9498    0.9363     17642
     Disease     0.8102    0.8715    0.8397     12355

   micro avg     0.8754    0.9176    0.8960     29997
   macro avg     0.8667    0.9107    0.8880     29997
weighted avg     0.8766    0.9176    0.8965     29997




# BERT+CRF - CDR

In [ ]:
cdr_bert_crf_model = create_bert_crf_model(CDR_NUM_LABELS, CDR_MAX_LENGTH)

Some layers from the model checkpoint at dslim/bert-large-NER were not used when initializing TFBertModel: ['dropout_73', 'classifier']
- This IS expected if you are initializing TFBertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFBertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
All the layers of TFBertModel were initialized from the model checkpoint at dslim/bert-large-NER.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFBertModel for predictions without further training.


In [ ]:
# Train with sample train/ validation dataset

history = cdr_bert_crf_model.fit([bert_cdr_train_input_ids[:100], bert_cdr_train_attention_mask[:100]], 
                                          bert_cdr_train_labels[:100], batch_size=8, epochs=5, 
                                          validation_data=([bert_cdr_val_input_ids[:100], bert_cdr_val_attention_mask[:100]], bert_cdr_val_labels[:100]))


Epoch 1/5


13/13 [==============================] - 52s 1s/step - loss: 105.9013 - accuracy: 0.8830 - val_loss_val: 34.5611 - val_val_accuracy: 0.9758
Epoch 2/5
13/13 [==============================] - 11s 847ms/step - loss: 31.4553 - accuracy: 0.9708 - val_loss_val: 23.2534 - val_val_accuracy: 0.9735
Epoch 3/5
13/13 [==============================] - 11s 830ms/step - loss: 22.5090 - accuracy: 0.9750 - val_loss_val: 20.6260 - val_val_accuracy: 0.9753
Epoch 4/5
13/13 [==============================] - 11s 829ms/step - loss: 17.1037 - accuracy: 0.9810 - val_loss_val: 16.3674 - val_val_accuracy: 0.9799
Epoch 5/5
13/13 [==============================] - 11s 832ms/step - loss: 13.5639 - accuracy: 0.9852 - val_loss_val: 14.3451 - val_val_accuracy: 0.9831


In [ ]:
# Train with full train/ validation dataset

history = cdr_bert_crf_model.fit([bert_cdr_train_input_ids, bert_cdr_train_attention_mask], 
                                          bert_cdr_train_labels, batch_size=8, epochs=5, 
                                          validation_data=([bert_cdr_val_input_ids, bert_cdr_val_attention_mask], bert_cdr_val_labels))

Epoch 1/5
571/571 [==============================] - 467s 819ms/step - loss: 8.6842 - accuracy: 0.9907 - val_loss_val: 6.7287 - val_val_accuracy: 0.9929
Epoch 2/5
571/571 [==============================] - 465s 815ms/step - loss: 4.8021 - accuracy: 0.9954 - val_loss_val: 5.8887 - val_val_accuracy: 0.9940
Epoch 3/5
571/571 [==============================] - 467s 819ms/step - loss: 3.3128 - accuracy: 0.9970 - val_loss_val: 5.9569 - val_val_accuracy: 0.9944
Epoch 4/5
571/571 [==============================] - 467s 818ms/step - loss: 2.3613 - accuracy: 0.9979 - val_loss_val: 6.3449 - val_val_accuracy: 0.9945
Epoch 5/5
571/571 [==============================] - 466s 816ms/step - loss: 1.8218 - accuracy: 0.9986 - val_loss_val: 7.0243 - val_val_accuracy: 0.9947


In [ ]:
#loss, accuracy = cdr_bert_crf_model.evaluate([bert_cdr_test_input_ids, bert_cdr_test_attention_mask], bert_cdr_test_labels, verbose=0)

cdr_bert_crf_predictions = cdr_bert_crf_model.predict([bert_cdr_test_input_ids, bert_cdr_test_attention_mask])

150/150 [==============================] - 54s 323ms/step


In [ ]:
print_classification_report(bert_cdr_test_labels, bert_cdr_test_attention_mask, cdr_bert_crf_predictions, cdr_label_list)

  0%|          | 0/4798 [00:00<?, ?it/s]

              precision    recall  f1-score   support

     Disease     0.8200    0.8564    0.8378     12301
        GENE     0.9313    0.9376    0.9344     17587

   micro avg     0.8845    0.9042    0.8942     29888
   macro avg     0.8757    0.8970    0.8861     29888
weighted avg     0.8855    0.9042    0.8947     29888



# BERT+BILSTM+CRF - CDR

In [ ]:
cdr_bert_bilstm_crf_model = create_bert_bilstm_crf_model(CDR_NUM_LABELS, 32, CDR_MAX_LENGTH)

NameError: ignored

In [ ]:
# Train with sample train/ validation dataset


history = cdr_bert_bilstm_crf_model.fit([bert_cdr_train_input_ids[:100], bert_cdr_train_attention_mask[:100]], 
                                          bert_cdr_train_labels[:100], batch_size=8, epochs=5, 
                                          validation_data=([bert_cdr_val_input_ids[:100], bert_cdr_val_attention_mask[:100]], bert_cdr_val_labels[:100]))


NameError: ignored

In [ ]:
# Train with full train/ validation dataset

history = cdr_bert_bilstm_crf_model.fit([bert_cdr_train_input_ids, bert_cdr_train_attention_mask], 
                                          bert_cdr_train_labels, batch_size=8, epochs=5, 
                                          validation_data=([bert_cdr_val_input_ids, bert_cdr_val_attention_mask], bert_cdr_val_labels))I 


SyntaxError: ignored

In [ ]:
#loss, accuracy = cdr_bert_bilstm_crf_model.evaluate([bert_cdr_test_input_ids, bert_cdr_test_attention_mask], bert_cdr_test_labels, verbose=0)

cdr_bert_bilstm_crf_predictions = cdr_bert_bilstm_crf_model.predict([bert_cdr_test_input_ids, bert_cdr_test_attention_mask])

150/150 [==============================] - 52s 343ms/step


In [ ]:
print_classification_report(bert_cdr_test_labels, bert_cdr_test_attention_mask, cdr_bert_bilstm_crf_predictions, cdr_label_list)

  0%|          | 0/4798 [00:00<?, ?it/s]

              precision    recall  f1-score   support

     Disease     0.8275    0.8224    0.8249     12301
        GENE     0.9187    0.9477    0.9330     17587

   micro avg     0.8820    0.8961    0.8890     29888
   macro avg     0.8731    0.8850    0.8789     29888
weighted avg     0.8812    0.8961    0.8885     29888




# BioBERT+CRF - CDR

In [182]:
cdr_biobert_crf_model = create_biobert_crf_model(CDR_NUM_LABELS, CDR_MAX_LENGTH)

Some weights of the PyTorch model were not used when initializing the TF 2.0 model TFBertModel: ['cls.predictions.transform.dense.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.predictions.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing TFBertModel from a PyTorch model trained on another task or with another architecture (e.g. initializing a TFBertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFBertModel from a PyTorch model that you expect to be exactly identical (e.g. initializing a TFBertForSequenceClassification model from a BertForSequenceClassification model).
All the weights of TFBertModel were initialized from the PyTorch model.
If your task is similar to the task the model of the checkpoint

In [183]:
# Train with sample train/ validation dataset

history = cdr_biobert_crf_model.fit([biobert_cdr_train_input_ids[:100], biobert_cdr_train_attention_mask[:100]], 
                                          biobert_cdr_train_labels[:100], batch_size=8, epochs=5, 
                                          validation_data=([biobert_cdr_val_input_ids[:100], biobert_cdr_val_attention_mask[:100]], biobert_cdr_val_labels[:100]))


Epoch 1/5


13/13 [==============================] - 30s 989ms/step - loss: 107.0280 - accuracy: 0.9124 - val_loss_val: 42.6963 - val_val_accuracy: 0.9758
Epoch 2/5
13/13 [==============================] - 8s 664ms/step - loss: 48.0468 - accuracy: 0.9677 - val_loss_val: 33.4867 - val_val_accuracy: 0.9759
Epoch 3/5
13/13 [==============================] - 9s 684ms/step - loss: 29.1313 - accuracy: 0.9716 - val_loss_val: 19.6926 - val_val_accuracy: 0.9797
Epoch 4/5
13/13 [==============================] - 9s 678ms/step - loss: 19.1925 - accuracy: 0.9812 - val_loss_val: 18.5973 - val_val_accuracy: 0.9790
Epoch 5/5
13/13 [==============================] - 9s 677ms/step - loss: 12.1265 - accuracy: 0.9866 - val_loss_val: 14.3175 - val_val_accuracy: 0.9846


In [184]:
# Train with full train/ validation dataset

history = cdr_biobert_crf_model.fit([biobert_cdr_train_input_ids, biobert_cdr_train_attention_mask], 
                                          biobert_cdr_train_labels, batch_size=8, epochs=5, 
                                          validation_data=([biobert_cdr_val_input_ids, biobert_cdr_val_attention_mask], biobert_cdr_val_labels))


Epoch 1/5
571/571 [==============================] - 375s 657ms/step - loss: 6.9972 - accuracy: 0.9926 - val_loss_val: 5.4096 - val_val_accuracy: 0.9947
Epoch 2/5
571/571 [==============================] - 375s 657ms/step - loss: 2.7594 - accuracy: 0.9972 - val_loss_val: 5.4527 - val_val_accuracy: 0.9950
Epoch 3/5
571/571 [==============================] - 375s 657ms/step - loss: 1.3717 - accuracy: 0.9986 - val_loss_val: 6.2769 - val_val_accuracy: 0.9950
Epoch 4/5
571/571 [==============================] - 375s 657ms/step - loss: 1.0205 - accuracy: 0.9990 - val_loss_val: 6.7816 - val_val_accuracy: 0.9952
Epoch 5/5
571/571 [==============================] - 375s 657ms/step - loss: 0.8246 - accuracy: 0.9992 - val_loss_val: 7.3245 - val_val_accuracy: 0.9954


In [185]:
#loss, accuracy = cdr_biobert_crf_model.evaluate([biobert_cdr_test_input_ids, biobert_cdr_test_attention_mask], biobert_cdr_test_labels, verbose=0)

cdr_biobert_crf_predictions = cdr_biobert_crf_model.predict([biobert_cdr_test_input_ids, biobert_cdr_test_attention_mask])

150/150 [==============================] - 33s 190ms/step


In [186]:
print_classification_report(biobert_cdr_test_labels, biobert_cdr_test_attention_mask, cdr_biobert_crf_predictions, cdr_label_list)

  0%|          | 0/4798 [00:00<?, ?it/s]

              precision    recall  f1-score   support

    Chemical     0.9324    0.9502    0.9412     17642
     Disease     0.8448    0.8560    0.8504     12355

   micro avg     0.8964    0.9114    0.9038     29997
   macro avg     0.8886    0.9031    0.8958     29997
weighted avg     0.8963    0.9114    0.9038     29997



# BioBERT+BILSTM+CRF - CDR

In [274]:
cdr_biobert_bilstm_crf_model = create_biobert_bilstm_crf_model(CDR_NUM_LABELS, 888, CDR_MAX_LENGTH)

Some weights of the PyTorch model were not used when initializing the TF 2.0 model TFBertModel: ['cls.predictions.transform.dense.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.predictions.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing TFBertModel from a PyTorch model trained on another task or with another architecture (e.g. initializing a TFBertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFBertModel from a PyTorch model that you expect to be exactly identical (e.g. initializing a TFBertForSequenceClassification model from a BertForSequenceClassification model).
All the weights of TFBertModel were initialized from the PyTorch model.
If your task is similar to the task the model of the checkpoint

In [275]:
# Train with sample train/ validation dataset

history = cdr_biobert_bilstm_crf_model.fit([biobert_cdr_train_input_ids[:100], biobert_cdr_train_attention_mask[:100]], 
                                          biobert_cdr_train_labels[:100], batch_size=8, epochs=5, 
                                          validation_data=([biobert_cdr_val_input_ids[:100], biobert_cdr_val_attention_mask[:100]], biobert_cdr_val_labels[:100]))


Epoch 1/5


13/13 [==============================] - 34s 1s/step - loss: 79.5949 - accuracy: 0.9556 - val_loss_val: 39.3198 - val_val_accuracy: 0.9758
Epoch 2/5
13/13 [==============================] - 9s 729ms/step - loss: 50.1957 - accuracy: 0.9580 - val_loss_val: 29.8365 - val_val_accuracy: 0.9752
Epoch 3/5
13/13 [==============================] - 9s 722ms/step - loss: 29.3822 - accuracy: 0.9680 - val_loss_val: 23.2935 - val_val_accuracy: 0.9765
Epoch 4/5
13/13 [==============================] - 9s 729ms/step - loss: 22.7127 - accuracy: 0.9735 - val_loss_val: 18.1995 - val_val_accuracy: 0.9797
Epoch 5/5
13/13 [==============================] - 9s 729ms/step - loss: 19.4346 - accuracy: 0.9757 - val_loss_val: 16.9535 - val_val_accuracy: 0.9794


In [276]:
# Train with full train/ validation dataset

history = cdr_biobert_bilstm_crf_model.fit([biobert_cdr_train_input_ids, biobert_cdr_train_attention_mask], 
                                          biobert_cdr_train_labels, batch_size=8, epochs=5, 
                                          validation_data=([biobert_cdr_val_input_ids, biobert_cdr_val_attention_mask], biobert_cdr_val_labels))

Epoch 1/5
571/571 [==============================] - 408s 715ms/step - loss: 7.5652 - accuracy: 0.9913 - val_loss_val: 6.0216 - val_val_accuracy: 0.9939
Epoch 2/5
571/571 [==============================] - 409s 716ms/step - loss: 3.0063 - accuracy: 0.9970 - val_loss_val: 5.8907 - val_val_accuracy: 0.9947
Epoch 3/5
571/571 [==============================] - 407s 714ms/step - loss: 2.0438 - accuracy: 0.9979 - val_loss_val: 5.6260 - val_val_accuracy: 0.9951
Epoch 4/5
571/571 [==============================] - 407s 712ms/step - loss: 1.1941 - accuracy: 0.9988 - val_loss_val: 6.6168 - val_val_accuracy: 0.9950
Epoch 5/5
571/571 [==============================] - 407s 712ms/step - loss: 0.7816 - accuracy: 0.9992 - val_loss_val: 7.5425 - val_val_accuracy: 0.9952


In [277]:
#loss, accuracy = cdr_biobert_bilstm_crf_model.evaluate([biobert_cdr_test_input_ids, biobert_cdr_test_attention_mask], biobert_cdr_test_labels, verbose=0)

cdr_biobert_bilstm_crf_predictions = cdr_biobert_bilstm_crf_model.predict([biobert_cdr_test_input_ids, biobert_cdr_test_attention_mask])

150/150 [==============================] - 35s 207ms/step


In [278]:
print_classification_report(biobert_cdr_test_labels, biobert_cdr_test_attention_mask, cdr_biobert_bilstm_crf_predictions, cdr_label_list)

  0%|          | 0/4798 [00:00<?, ?it/s]

              precision    recall  f1-score   support

    Chemical     0.9420    0.9370    0.9395     17642
     Disease     0.8608    0.8385    0.8495     12355

   micro avg     0.9090    0.8964    0.9027     29997
   macro avg     0.9014    0.8877    0.8945     29997
weighted avg     0.9086    0.8964    0.9024     29997




# CUSTOM LOSS FUNCTION

In [ ]:
## Implementing the custom CRF layer, loss, and model


class CRFLayer(Layer):
  """
  Computes the log likelihood during training
  Performs Viterbi decoding during prediction
  """
  def __init__(self,
               label_size=3, mask_id=0,
               trans_params=None, 
               name='crf',
               **kwargs):
    super(CRFLayer, self).__init__(name=name, **kwargs)
    self.label_size = label_size
    self.mask_id = mask_id
    self.transition_params = None
    
    if trans_params is None:  # not reloading pretrained params
        self.transition_params = tf.Variable(
tf.random.uniform(shape=(label_size, label_size)),
                trainable=False)
    else:
        self.transition_params = trans_params

  """
  A custom loss function for NER using a CRF
  """
  def loss(self, y_true, y_pred):
    y_pred = tf.convert_to_tensor(y_pred)
    y_true = tf.cast(self.get_proper_labels(y_true), y_pred.dtype)
    seq_lengths = self.get_seq_lengths(y_true)
    log_likelihoods, self.transition_params = tfa.text.crf_log_likelihood(y_pred, y_true, seq_lengths)
    # save transition params
    self.transition_params = tf.Variable(self.transition_params, 
      trainable=False)
    # calc loss
    loss = - tf.reduce_mean(log_likelihoods)
    return loss


def crf_loss_func(potentials, sequence_length, kernel, y):
    crf_likelihood, _ = tfa.text.crf_log_likelihood(
        potentials, y, sequence_length, kernel
    )
    # likelihood to loss
    flat_crf_loss = -1 * crf_likelihood
    crf_loss = tf.reduce_mean(flat_crf_loss)

    return crf_loss

# Scratch section

In [ ]:
# @title Create Unified Label Mapping Across Datasets
# rename "tags" to "ner_tags" for consistency
if 'tags' in cdr_dataset['train'].features.keys():
  cdr_dataset = cdr_dataset.rename_column("tags", "ner_tags")

# get labels from each dataset
ncbi_label_names = ncbi_dataset["train"].features["ner_tags"].feature.names
gm_label_names = gm_dataset["train"].features["ner_tags"].feature.names
cdr_label_names = ['O', 'B-Chemical', 'B-Disease', 'I-Disease', 'I-Chemical']

# create an unified label-to-index mapping across datasets
# keys: unique labels, values: indexes
label2index = {}
id = 0
for n in ncbi_label_names + gm_label_names + cdr_label_names:
  if n not in label2index:
    label2index[n] = id
    id += 1

label_names = list(label2index.keys())
label2index

from datasets import Features, Value, Sequence, ClassLabel
# define wanted output columns from the mapping process
# this ensures that the tokenized datasets have the same features for concatenation 
features = Features({
  'id': Value(dtype='string', id=None),
  'tokens': Sequence(feature=Value(dtype='string', id=None), length=-1, id=None),
  'ner_tags': Sequence(feature=ClassLabel(names=label_names, id=None), length=-1, id=None),
  'input_ids': Sequence(feature=Value(dtype='int32', id=None), length=-1, id=None),
  'token_type_ids': Sequence(feature=Value(dtype='int8', id=None), length=-1, id=None),
  'attention_mask': Sequence(feature=Value(dtype='int8', id=None), length=-1, id=None),
  'labels': Sequence(feature=Value(dtype='int64', id=None), length=-1, id=None)
})

bert_tokenizer = AutoTokenizer.from_pretrained("dslim/bert-base-NER")
# @title Map Labels To Tokenized Data (The Original Labels Were At Word-Level)
def bert_process(data, label_names, label2index):
  inputs = bert_tokenizer(data['tokens'], is_split_into_words=True, add_special_tokens=False)
  tags = []
  ids = []
  for i, labels in enumerate(data['ner_tags']):
    # len(word_id) = len(tokens)
    # word_id indicates which word the token belongs to
    word_ids = inputs.word_ids(i)
    label_ids = []
    for wid in word_ids:
      # set label to -100 for CLS and SEP tokens
      if wid is None: 
        label_ids.append(-100)
      else:
        # original label at word-level
        orig_label_index = labels[wid]  
        orig_label_name = label_names[orig_label_index]
        # grab the new unified label indexes
        new_label_index = label2index[orig_label_name]
        label_ids.append(new_label_index)
    tags.append(label_ids)
    # overwrite ids to ensure we have all the features defined above
    # cdr data doesn't have ids
    ids.append('0')
  inputs['id'] = ids
  # the new labels for model training
  inputs['labels'] = tags
  return inputs

biobert_tokenizer = AutoTokenizer.from_pretrained("dmis-lab/biobert-base-cased-v1.2")
# @title Map Labels To Tokenized Data (The Original Labels Were At Word-Level)
def biobert_process(data, label_names, label2index):
  inputs = biobert_tokenizer(data['tokens'], is_split_into_words=True, add_special_tokens=False)
  tags = []
  ids = []
  for i, labels in enumerate(data['ner_tags']):
    # len(word_id) = len(tokens)
    # word_id indicates which word the token belongs to
    word_ids = inputs.word_ids(i)
    label_ids = []
    for wid in word_ids:
      # set label to -100 for CLS and SEP tokens
      if wid is None: 
        label_ids.append(-100)
      else:
        # original label at word-level
        orig_label_index = labels[wid]  
        orig_label_name = label_names[orig_label_index]
        # grab the new unified label indexes
        new_label_index = label2index[orig_label_name]
        label_ids.append(new_label_index)
    tags.append(label_ids)
    # overwrite ids to ensure we have all the features defined above
    # cdr data doesn't have ids
    ids.append('0')
  inputs['id'] = ids
  # the new labels for model training
  inputs['labels'] = tags
  return inputs

In [ ]:
ncbi_train_data = ncbi_dataset['train']
ncbi_validation_data = ncbi_dataset['validation']
ncbi_test_data = ncbi_dataset['test']

ncbi_dataset_train_examples = ncbi_dataset['train']['tokens']
ncbi_dataset_train_labels = ncbi_dataset['train']['ner_tags']

ncbi_dataset_validation_examples = ncbi_dataset['validation']['tokens']
ncbi_dataset_validation_labels = ncbi_dataset['validation']['ner_tags']

ncbi_dataset_test_examples = ncbi_dataset['test']['tokens']
ncbi_dataset_test_labels = ncbi_dataset['test']['ner_tags']

In [ ]:
biobert_tokenizer(ncbi_dataset_train_examples[0])

{'input_ids': [[101, 9117, 102], [101, 1104, 102], [101, 170, 1643, 1665, 1477, 102], [101, 117, 102], [101, 170, 102], [101, 16358, 3702, 12733, 102], [101, 1104, 102], [101, 1103, 102], [101, 8050, 26601, 21943, 2285, 102], [101, 185, 23415, 5674, 4863, 102], [101, 1884, 2646, 102], [101, 189, 27226, 102], [101, 17203, 1766, 102], [101, 119, 102]], 'token_type_ids': [[0, 0, 0], [0, 0, 0], [0, 0, 0, 0, 0, 0], [0, 0, 0], [0, 0, 0], [0, 0, 0, 0, 0], [0, 0, 0], [0, 0, 0], [0, 0, 0, 0, 0, 0], [0, 0, 0, 0, 0, 0], [0, 0, 0, 0], [0, 0, 0, 0], [0, 0, 0, 0], [0, 0, 0]], 'attention_mask': [[1, 1, 1], [1, 1, 1], [1, 1, 1, 1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1, 1, 1], [1, 1, 1], [1, 1, 1], [1, 1, 1, 1, 1, 1], [1, 1, 1, 1, 1, 1], [1, 1, 1, 1], [1, 1, 1, 1], [1, 1, 1, 1], [1, 1, 1]]}

In [ ]:
data_collator = DataCollatorForTokenClassification(tokenizer=biobert_tokenizer)
training_args = TrainingArguments("test-trainer")
#biobert_model = 'dmis-lab/biobert-base-cased-v1.2'
#ncbi_biobert_model = AutoModelForTokenClassification.from_pretrained(biobert_model, num_labels=len(ncbi_label_list))

#biobert_bilstm_crf_ncbi_trainer = Trainer(
#    biobert_bilstm_crf_model,
#    training_args,
#    train_dataset = tokenized_ncbi_dataset["train"],
#    eval_dataset = tokenized_ncbi_dataset["validation"],
#    data_collator = data_collator,
#    tokenizer = biobert_tokenizer,
#)

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).


In [ ]:
def biobert_bilstm_crf_model(hidden_size = 100, 
                             output_size = 5,
                             learning_rate = 0.003, 
                             dropout = 0.3,
                             max_length = 20):

    
    input_ids = tf.keras.layers.Input(shape=(max_length,), dtype='int32', name='input_id')
    input_mask = tf.keras.layers.Input(shape=(max_length,), dtype='int32', name="input_masks")
    input_secdrent = tf.keras.layers.Input(shape=(max_length,), dtype='int32', name="segment_ids")

    biobert_inputs = [input_ids, input_mask, input_segment]

    biobert_layer = AutoModel.from_pretrained("dmis-lab/biobert-base-cased-v1.2")

    #biobert_sequence = biobert_layer(biobert_inputs)[0]

    biobert_output = biobert_layer(input_ids)
    #last_hidden_states = biobert_output[0]

    bilstm_layer = Bidirectional(LSTM(hidden_size, return_sequences=True), merge_mode = "sum")
    bilstm_layer_out = bilstm_layer(Dropout(0.5)(biobert_output))

    crf = CRF(dtype='float32', sparse_target=True)
    crf_output = crf(BatchNormalization()(bilstm_layer_out))

    base_model = keras.Model(input=input_ids, output=crf_output)
    model = ModelWithCRFLoss(base_model)

    optimizer = keras.optimizers.Adam(learning_rate = learning_rate)

    model.compile(optimizer=optimizer)

    model.summary()

    return model

In [ ]:
model = biobert_bilstm_crf_model()

In [ ]:
sample = model.fit(sample_train_encodings, sample_train_labels, validation_data=(sample_val_encodings, sample_val_labels), batch_size=8, epochs=1)

In [ ]:
#model = create_biobert_bilstm_crf_model(input_length, hidden_size, output_size, learning_rate)
#history = model.fit(input_ids)

['[CLS]', 'identification', 'of', 'a', '##p', '##c', '##2', ',', 'a', 'ho', '##mo', '##logue', 'of', 'the', 'ad', '##eno', '##mat', '##ous', 'p', '##oly', '##po', '##sis', 'co', '##li', 't', '##umour', 'suppress', '##or', '.', '[SEP]']


In [ ]:
model.fit(
    biobert_bilstm_crf_model, 
    {"ner": ncbi_labels },
    validation_data=(bert_inputs_test_k, {"ner": ncbi_labels }),
    epochs=5,
    batch_size=16

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
loading configuration file config.json from cache at /root/.cache/huggingface/hub/models--dmis-lab--biobert-base-cased-v1.2/snapshots/67c9c25b46986521ca33df05d8540da1210b3256/config.json
Model config BertConfig {
  "_name_or_path": "dmis-lab/biobert-base-cased-v1.2",
  "architectures": [
    "BertForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "classifier_dropout": null,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "id2label": {
    "0": "LABEL_0",
    "1": "LABEL_1",
    "2": "LABEL_2"
  },
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "label2id": {
    "LABEL_0": 0,
    "LABEL_1": 1,
    "LABEL_2": 2
  },
  "layer_norm_eps": 1e-12,
  "m

AttributeError: ignored

In [ ]:

def bert_tweets_model():
    bert_encoder = TFBertModel.from_pretrained(model_name)
    input_word_ids = tf.keras.Input(shape=(max_length,), dtype=tf.int32, name="input_ids")
    last_hidden_states = bert_encoder(input_word_ids)[0]    
    x = tf.keras.layers.LSTM(100, dropout=0.3, recurrent_dropout=0.3)(last_hidden_states)
    output = tf.keras.layers.Dense(1, activation='sigmoid')(x)
    model = tf.keras.Model(inputs=input_word_ids, outputs=output)
    
    return model

class CustomBERT_NER_LSTM_Model(tf.keras.layers.Layer):
    def __init__(self):
          super(CustomBERT_NER_Model, self).__init__()
          self.bert_NER = AutoModelForTokenClassification.from_pretrained("dslim/bert-base-NER")
          ### New layers:
          self.lstm = nn.LSTM(768, 256, batch_first=True,bidirectional=True)
          self.linear = nn.Linear(256*2, 3)
          

    def forward(self, ids, mask):
          sequence_output, pooled_output = self.bert_NER(
               ids, 
               attention_mask=mask)

          # sequence_output has the following shape: (batch_size, sequence_length, 768)
          lstm_output, (h,c) = self.lstm(sequence_output) ## extract the 1st token's embeddings
          hidden = torch.cat((lstm_output[:,-1, :256],lstm_output[:,0, 256:]),dim=-1)
          linear_output = self.linear(hidden.view(-1,256*2)) ### assuming that you are only using the output of the last LSTM cell to perform classification

          return linear_output

bert_NER_tokenizer = AutoTokenizer.from_pretrained("dslim/bert-base-NER")
bert_NER_LSTM_Model = CustomBERT_NER_LSTM_Model()

NameError: ignored